# R Feature Engeneering BGP onehot coding and log transformation 060620222

In [2]:
#library(dplyr)
#library(dbplyr)
#library(tidyverse)
#library(DBI)
#library(odbc)

## A. Up loading the FF from SQL to data frame : DF_BGP_CFF

In [3]:

conn <- DBI::dbConnect(
  odbc::odbc(),
  Driver = "SQL Server",
  Server = "SHEM\\SQLEXPRESS",
  Database = "A_BDG"
)

In [4]:
DF_BGP_CFF <- dbGetQuery(conn, "SELECT * FROM DF_BGP_CFF")

In [5]:
DF_BGP_CFF

BIDm                         SIDn    PrUs                         
1     Apr_Bobcat_assembly_Adam     Bobcat  Entertainment/public assembly
2     Apr_Bobcat_assembly_Billy    Bobcat  Entertainment/public assembly
3     Apr_Bobcat_assembly_Camilla  Bobcat  Entertainment/public assembly
4     Apr_Bobcat_assembly_Franklin Bobcat  Entertainment/public assembly
5     Apr_Bobcat_education_Alissa  Bobcat  Education                    
6     Apr_Bobcat_education_Angela  Bobcat  Education                    
7     Apr_Bobcat_education_Barbra  Bobcat  Education                    
8     Apr_Bobcat_education_Coleman Bobcat  Education                    
9     Apr_Bobcat_education_Dylan   Bobcat  Education                    
10    Apr_Bobcat_education_Emile   Bobcat  Education                    
11    Apr_Bobcat_education_Hollis  Bobcat  Education                    
12    Apr_Bobcat_education_Jayne   Bobcat  Education                    
13    Apr_Bobcat_education_Karin   Bobcat  Education                    
14    Apr_Bobcat_education_Marisha Bobcat  Education                    
15    Apr_Bobcat_education_Miki    Bobcat  Education                    
16    Apr_Bobcat_education_Monte   Bobcat  Education                    
17    Apr_Bobcat_education_Rodrick Bobcat  Education                    
18    Apr_Bobcat_education_Rosalva Bobcat  Education                    
19    Apr_Bobcat_education_Toni    Bobcat  Education                    
20    Apr_Bobcat_education_Whitney Bobcat  Education                    
21    Apr_Bobcat_lodging_Darin     Bobcat  Lodging/residential          
22    Apr_Bobcat_lodging_Melaine   Bobcat  Lodging/residential          
23    Apr_Bobcat_lodging_Nickolas  Bobcat  Lodging/residential          
24    Apr_Bobcat_office_Alma       Bobcat  Office                       
25    Apr_Bobcat_office_Justine    Bobcat  Office                       
26    Apr_Bobcat_office_Kassandra  Bobcat  Office                       
27    Apr_Bobcat_office_Melody     Bobcat  Office                       
28    Apr_Bobcat_office_Nikita     Bobcat  Office                       
29    Apr_Bobcat_other_Howard      Bobcat  Other                        
30    Apr_Bobcat_other_Jovita      Bobcat  Other                        
...   ...                          ...     ...                          
10243 Sep_Peacock_office_Dara      Peacock Office                       
10244 Sep_Peacock_office_Effie     Peacock Office                       
10245 Sep_Peacock_office_Elton     Peacock Office                       
10246 Sep_Peacock_office_Glenn     Peacock Office                       
10247 Sep_Peacock_office_Jonathon  Peacock Office                       
10248 Sep_Peacock_office_Julian    Peacock Office                       
10249 Sep_Peacock_office_Major     Peacock Office                       
10250 Sep_Peacock_office_Naomi     Peacock Office                       
10251 Sep_Peacock_office_Norman    Peacock Office                       
10252 Sep_Peacock_public_Kelvin    Peacock Public services              
10253 Sep_Peacock_public_Linda     Peacock Public services              
10254 Sep_Swan_unknown_Allison     Swan    miss                         
10255 Sep_Swan_unknown_Andres      Swan    miss                         
10256 Sep_Swan_unknown_Bette       Swan    miss                         
10257 Sep_Swan_unknown_Christoper  Swan    miss                         
10258 Sep_Swan_unknown_Douglas     Swan    miss                         
10259 Sep_Swan_unknown_Esteban     Swan    miss                         
10260 Sep_Swan_unknown_Fabian      Swan    miss                         
10261 Sep_Swan_unknown_Ike         Swan    miss                         
10262 Sep_Swan_unknown_Isaiah      Swan    miss                         
10263 Sep_Swan_unknown_Jan         Swan    miss                         
10264 Sep_Swan_unknown_Jerold      Swan    miss                         
10265 Sep_Swan_unknown_Noelia      Swan    miss                 

### A.1.  Descriptive Statistics

In [7]:
summary(DF_BGP_CFF)

     BIDm               SIDn               PrUs              SbPrUs         
 Length:10272       Length:10272       Length:10272       Length:10272      
 Class :character   Class :character   Class :character   Class :character  
 Mode  :character   Mode  :character   Mode  :character   Mode  :character  
                                                                            
                                                                            
                                                                            
      sqm               lat             lng              Tmz           
 Min.   :   26.3   Min.   :28.52   Min.   :-111.93   Length:10272      
 1st Qu.: 3446.6   1st Qu.:30.27   1st Qu.: -97.74   Class :character  
 Median : 6929.8   Median :40.35   Median : -93.26   Mode  :character  
 Mean   :10196.6   Mean   :37.46   Mean   : -89.96                     
 3rd Qu.:13020.9   3rd Qu.:44.98   3rd Qu.: -76.49                     
 Max.   :80038.2   Max.   :45

### A.2 Strings to factors
### A.2.1 Create list for string columns (strlst) and for numeric columns (numlst)

In [6]:
### creating a name list of the features separating chars (strlst) features from numeric ones (numlst)
strlst <- NULL
numlst <- NULL
for (v in names(DF_BGP_CFF)) {
    if(typeof(DF_BGP_CFF[[v]])=='character' | is.factor(DF_BGP_CFF[[v]])) {
        strlst <- c(strlst,v) 
    } else {
        numlst <- c(numlst, v)
    }
}
strlst
numlst

[1] "BIDm"            "SIDn"            "PrUs"            "SbPrUs"         
 [5] "Tmz"             "gas_Max_W1"      "gas_Max_W2"      "gas_Max_W3"     
 [9] "gas_Max_W4"      "gas_Max_W5"      "gas_Min_W1"      "gas_Min_W2"     
[13] "gas_Min_W3"      "gas_Min_W4"      "gas_Min_W5"      "gas_AVG_W1"     
[17] "gas_AVG_W2"      "gas_AVG_W3"      "gas_AVG_W4"      "gas_AVG_W5"     
[21] "gas_STD_W1"      "gas_STD_W2"      "gas_STD_W3"      "gas_STD_W4"     
[25] "gas_STD_W5"      "hotwater_Max_W1" "hotwater_Max_W2" "hotwater_Max_W3"
[29] "hotwater_Max_W4" "hotwater_Max_W5" "hotwater_Min_W1" "hotwater_Min_W2"
[33] "hotwater_Min_W3" "hotwater_Min_W4" "hotwater_Min_W5" "hotwater_AVG_W1"
[37] "hotwater_AVG_W2" "hotwater_AVG_W3" "hotwater_AVG_W4" "hotwater_AVG_W5"
[41] "hotwater_STD_W1" "hotwater_STD_W2" "hotwater_STD_W3" "hotwater_STD_W4"
[45] "hotwater_STD_W5" "Stm_Max_W1"      "Stm_Max_W2"      "Stm_Max_W3"     
[49] "Stm_Max_W4"      "Stm_Max_W5"      "Stm_Min_W1"      "Stm_Min_W2"     
[53] "Stm_Min_W3"      "Stm_Min_W4"      "Stm_Min_W5"      "Stm_AVG_W1"     
[57] "Stm_AVG_W2"      "Stm_AVG_W3"      "Stm_AVG_W4"      "Stm_AVG_W5"     
[61] "Stm_STD_W1"      "Stm_STD_W2"      "Stm_STD_W3"      "Stm_STD_W4"     
[65] "Stm_STD_W5"

[1] "sqm"                   "lat"                   "lng"                  
  [4] "El_Max_W1"             "El_Max_W2"             "El_Max_W3"            
  [7] "El_Max_W4"             "El_Max_W5"             "El_Min_W1"            
 [10] "El_Min_W2"             "El_Min_W3"             "El_Min_W4"            
 [13] "El_Min_W5"             "El_AVG_W1"             "El_AVG_W2"            
 [16] "El_AVG_W3"             "El_AVG_W4"             "El_AVG_W5"            
 [19] "El_STD_W1"             "El_STD_W2"             "El_STD_W3"            
 [22] "El_STD_W4"             "El_STD_W5"             "ChWt_Max_W1"          
 [25] "ChWt_Max_W2"           "ChWt_Max_W3"           "ChWt_Max_W4"          
 [28] "ChWt_Max_W5"           "ChWt_Min_W1"           "ChWt_Min_W2"          
 [31] "ChWt_Min_W3"           "ChWt_Min_W4"           "ChWt_Min_W5"          
 [34] "ChWt_AVG_W1"           "ChWt_AVG_W2"           "ChWt_AVG_W3"          
 [37] "ChWt_AVG_W4"           "ChWt_AVG_W5"           "ChWt_STD_W1"          
 [40] "ChWt_STD_W2"           "ChWt_STD_W3"           "ChWt_STD_W4"          
 [43] "ChWt_STD_W5"           "MAX_airTemperature_W1" "MAX_airTemperature_W2"
 [46] "MAX_airTemperature_W3" "MAX_airTemperature_W4" "MAX_airTemperature_W5"
 [49] "MAX_dewTemperature_W1" "MAX_dewTemperature_W2" "MAX_dewTemperature_W3"
 [52] "MAX_dewTemperature_W4" "MAX_dewTemperature_W5" "MAX_seaLvlPressure_W1"
 [55] "MAX_seaLvlPressure_W2" "MAX_seaLvlPressure_W3" "MAX_seaLvlPressure_W4"
 [58] "MAX_seaLvlPressure_W5" "MAX_windDirection_W1"  "MAX_windDirection_W2" 
 [61] "MAX_windDirection_W3"  "MAX_windDirection_W4"  "MAX_windDirection_W5" 
 [64] "MAX_windSpeed_W1"      "MAX_windSpeed_W2"      "MAX_windSpeed_W3"     
 [67] "MAX_windSpeed_W4"      "MAX_windSpeed_W5"      "Min_airTemperature_W1"
 [70] "Min_airTemperature_W2" "Min_airTemperature_W3" "Min_airTemperature_W4"
 [73] "Min_airTemperature_W5" "Min_dewTemperature_W1" "Min_dewTemperature_W2"
 [76] "Min_dewTemperature_W3" "Min_dewTemperature_W4" "Min_dewTemperature_W5"
 [79] "Min_seaLvlPressure_W1" "Min_seaLvlPressure_W2" "Min_seaLvlPressure_W3"
 [82] "Min_seaLvlPressure_W4" "Min_seaLvlPressure_W5" "Min_windDirection_W1" 
 [85] "Min_windDirection_W2"  "Min_windDirection_W3"  "Min_windDirection_W4" 
 [88] "Min_windDirection_W5"  "Min_windSpeed_W1"      "Min_windSpeed_W2"     
 [91] "Min_windSpeed_W3"      "Min_windSpeed_W4"      "Min_windSpeed_W5"     
 [94] "Avg_airTemperature_W1" "Avg_airTemperature_W2" "Avg_airTemperature_W3"
 [97] "Avg_airTemperature_W4" "Avg_airTemperature_W5" "Avg_dewTemperature_W1"
[100] "Avg_dewTemperature_W2" "Avg_dewTemperature_W3" "Avg_dewTemperature_W4"
[103] "Avg_dewTemperature_W5" "Avg_seaLvlPressure_W1" "Avg_seaLvlPressure_W2"
[106] "Avg_seaLvlPressure_W3" "Avg_seaLvlPressure_W4" "Avg_seaLvlPressure_W5"
[109] "Avg_windDirection_W1"  "Avg_windDirection_W2"  "Avg_windDirection_W3" 
[112] "Avg_windDirection_W4"  "Avg_windDirection_W5"  "Avg_windSpeed_W1"     
[115] "Avg_windSpeed_W2"      "Avg_windSpeed_W3"      "Avg_windSpeed_W4"     
[118] "Avg_windSpeed_W5"      "Std_airTemperature_W1" "Std_airTemperature_W2"
[121] "Std_airTemperature_W3" "Std_airTemperature_W4" "Std_airTemperature_W5"
[124] "Std_dewTemperature_W1" "Std_dewTemperature_W2" "Std_dewTemperature_W3"
[127] "Std_dewTemperature_W4" "Std_dewTemperature_W5" "Std_seaLvlPressure_W1"
[130] "Std_seaLvlPressure_W2" "Std_seaLvlPressure_W3" "Std_seaLvlPressure_W4"
[133] "Std_seaLvlPressure_W5" "Std_windDirection_W1"  "Std_windDirection_W2" 
[136] "Std_windDirection_W3"  "Std_windDirection_W4"  "Std_windDirection_W5" 
[139] "Std_windSpeed_W1"      "Std_windSpeed_W2"      "Std_windSpeed_W3"     
[142] "Std_windSpeed_W4"      "Std_windSpeed_W5"      "El_Nxt_Mnth_Avg_OC"

In [7]:
length(strlst)

[1] 65

In [8]:
length(numlst)

[1] 144

###  A.2.2 Change char featuers to factor

In [12]:
for (v in strlst) {
    if(typeof(DF_BGP_CFF[[v]])=='character') {
        DF_BGP_CFF[[v]] <- factor(DF_BGP_CFF[[v]])
    }
}

In [13]:
summary(DF_BGP_CFF)

                           BIDm             SIDn     
 Apr_Bobcat_assembly_Adam    :    1   Hog     :1824  
 Apr_Bobcat_assembly_Billy   :    1   Fox     :1644  
 Apr_Bobcat_assembly_Camilla :    1   Bull    :1476  
 Apr_Bobcat_assembly_Franklin:    1   Cockatoo:1404  
 Apr_Bobcat_education_Alissa :    1   Eagle   :1272  
 Apr_Bobcat_education_Angela :    1   Panther :1260  
 (Other)                     :10266   (Other) :1392  
                            PrUs                     SbPrUs    
 Education                    :3600   Office            :2532  
 Office                       :2544   College Classroom :1296  
 Lodging/residential          :1452   College Laboratory:1164  
 Entertainment/public assembly:1068   Dormitory         : 960  
 Public services              : 348   Research          : 348  
 miss                         : 228   Classroom         : 324  
 (Other)                      :1032   (Other)           :3648  
      sqm               lat             lng             

In [277]:
write.csv(summary(DF_BGP_CFF), file="BGP_CFF_sum_06062022.csv")

### A.3. Add index to be used insted of BIDn - char/ factor in to number.

In [14]:
DF_BGP_CFF_indx <- cbind(ID = 1:nrow(DF_BGP_CFF), DF_BGP_CFF)  # creating an index column for easy use without BIDm

In [15]:
DF_BGP_CFF_indx

ID    BIDm                         SIDn    PrUs                         
1      1    Apr_Bobcat_assembly_Adam     Bobcat  Entertainment/public assembly
2      2    Apr_Bobcat_assembly_Billy    Bobcat  Entertainment/public assembly
3      3    Apr_Bobcat_assembly_Camilla  Bobcat  Entertainment/public assembly
4      4    Apr_Bobcat_assembly_Franklin Bobcat  Entertainment/public assembly
5      5    Apr_Bobcat_education_Alissa  Bobcat  Education                    
6      6    Apr_Bobcat_education_Angela  Bobcat  Education                    
7      7    Apr_Bobcat_education_Barbra  Bobcat  Education                    
8      8    Apr_Bobcat_education_Coleman Bobcat  Education                    
9      9    Apr_Bobcat_education_Dylan   Bobcat  Education                    
10    10    Apr_Bobcat_education_Emile   Bobcat  Education                    
11    11    Apr_Bobcat_education_Hollis  Bobcat  Education                    
12    12    Apr_Bobcat_education_Jayne   Bobcat  Education                    
13    13    Apr_Bobcat_education_Karin   Bobcat  Education                    
14    14    Apr_Bobcat_education_Marisha Bobcat  Education                    
15    15    Apr_Bobcat_education_Miki    Bobcat  Education                    
16    16    Apr_Bobcat_education_Monte   Bobcat  Education                    
17    17    Apr_Bobcat_education_Rodrick Bobcat  Education                    
18    18    Apr_Bobcat_education_Rosalva Bobcat  Education                    
19    19    Apr_Bobcat_education_Toni    Bobcat  Education                    
20    20    Apr_Bobcat_education_Whitney Bobcat  Education                    
21    21    Apr_Bobcat_lodging_Darin     Bobcat  Lodging/residential          
22    22    Apr_Bobcat_lodging_Melaine   Bobcat  Lodging/residential          
23    23    Apr_Bobcat_lodging_Nickolas  Bobcat  Lodging/residential          
24    24    Apr_Bobcat_office_Alma       Bobcat  Office                       
25    25    Apr_Bobcat_office_Justine    Bobcat  Office                       
26    26    Apr_Bobcat_office_Kassandra  Bobcat  Office                       
27    27    Apr_Bobcat_office_Melody     Bobcat  Office                       
28    28    Apr_Bobcat_office_Nikita     Bobcat  Office                       
29    29    Apr_Bobcat_other_Howard      Bobcat  Other                        
30    30    Apr_Bobcat_other_Jovita      Bobcat  Other                        
...   ...   ...                          ...     ...                          
10243 10243 Sep_Peacock_office_Dara      Peacock Office                       
10244 10244 Sep_Peacock_office_Effie     Peacock Office                       
10245 10245 Sep_Peacock_office_Elton     Peacock Office                       
10246 10246 Sep_Peacock_office_Glenn     Peacock Office                       
10247 10247 Sep_Peacock_office_Jonathon  Peacock Office                       
10248 10248 Sep_Peacock_office_Julian    Peacock Office                       
10249 10249 Sep_Peacock_office_Major     Peacock Office                       
10250 10250 Sep_Peacock_office_Naomi     Peacock Office                       
10251 10251 Sep_Peacock_office_Norman    Peacock Office                       
10252 10252 Sep_Peacock_public_Kelvin    Peacock Public services              
10253 10253 Sep_Peacock_public_Linda     Peacock Public services              
10254 10254 Sep_Swan_unknown_Allison     Swan    miss                         
10255 10255 Sep_Swan_unknown_Andres      Swan    miss                         
10256 10256 Sep_Swan_unknown_Bette       Swan    miss                         
10257 10257 Sep_Swan_unknown_Christoper  Swan    miss                         
10258 10258 Sep_Swan_unknown_Douglas     Swan    miss                         
10259 10259 Sep_Swan_unknown_Esteban     Swan    miss                         
10260 10260 Sep_Swan_unknown_Fabian      Swan    miss                         
10261 10261 Sep_Swan_unknown_Ike         Swan    miss   

In [280]:
write.csv(DF_BGP_CFF_indx, file="DF_BGP_CFF_indx_06062022.csv")

### A.4. One hot encoding to factorized and charracters columns
#### A.4.1 Preparing the string list and the data to be one hot encoding

In [54]:
#library(caret) # for one hot encoding


In [281]:
stls_noBIDn <- strlst[2:65] # string list witout the BIDn Column - replased with index

In [282]:
temp1_OHC <-DF_BGP_CFF_indx[,c('ID',stls_noBIDn)] # temp df for creating one hot encoding only on the str columns

In [70]:
?dummyVars

#### A.4.2 Using dummyVars model to create the one hot encoding columns

In [283]:
dummy <- dummyVars(" ~ .", data=temp1_OHC)
temp2_OHC <- data.frame(predict(dummy, newdata = temp1_OHC)) 

In [284]:
temp2_OHC # the one hot encoding dataframe

ID    SIDn.Bobcat SIDn.Bull SIDn.Cockatoo SIDn.Crow SIDn.Eagle SIDn.Fox
1      1    1           0         0             0         0          0       
2      2    1           0         0             0         0          0       
3      3    1           0         0             0         0          0       
4      4    1           0         0             0         0          0       
5      5    1           0         0             0         0          0       
6      6    1           0         0             0         0          0       
7      7    1           0         0             0         0          0       
8      8    1           0         0             0         0          0       
9      9    1           0         0             0         0          0       
10    10    1           0         0             0         0          0       
11    11    1           0         0             0         0          0       
12    12    1           0         0             0         0          0       
13    13    1           0         0             0         0          0       
14    14    1           0         0             0         0          0       
15    15    1           0         0             0         0          0       
16    16    1           0         0             0         0          0       
17    17    1           0         0             0         0          0       
18    18    1           0         0             0         0          0       
19    19    1           0         0             0         0          0       
20    20    1           0         0             0         0          0       
21    21    1           0         0             0         0          0       
22    22    1           0         0             0         0          0       
23    23    1           0         0             0         0          0       
24    24    1           0         0             0         0          0       
25    25    1           0         0             0         0          0       
26    26    1           0         0             0         0          0       
27    27    1           0         0             0         0          0       
28    28    1           0         0             0         0          0       
29    29    1           0         0             0         0          0       
30    30    1           0         0             0         0          0       
...   ...   ...         ...       ...           ...       ...        ...     
10243 10243 0           0         0             0         0          0       
10244 10244 0           0         0             0         0          0       
10245 10245 0           0         0             0         0          0       
10246 10246 0           0         0             0         0          0       
10247 10247 0           0         0             0         0          0       
10248 10248 0           0         0             0         0          0       
10249 10249 0           0         0             0         0          0       
10250 10250 0           0         0             0         0          0       
10251 10251 0           0         0             0         0          0       
10252 10252 0           0         0             0         0          0       
10253 10253 0           0         0             0         0          0       
10254 10254 0           0         0             0         0          0       
10255 10255 0           0         0             0         0          0       
10256 10256 0           0         0             0         0          0       
10257 10257 0           0         0             0         0          0       
10258 10258 0           0         0             0         0          0       
10259 10259 0           0         0             0         0          0       
10260 10260 0           0         0             0         0          0       
10261 10261 0           0         0             0         0          0       
10262 10262 0           0   

#### A.4.3 Inputing the new columns with one hot encoding in to the indexd full data frame.

In [285]:
DF_BGP_OHC_index<-left_join(DF_BGP_CFF_indx,temp2_OHC,by='ID') # df_temp2 data frame with ID index and all the data and ONE HOT ENCODING

In [286]:
DF_BGP_OHC_index

ID    BIDm                         SIDn    PrUs                         
1      1    Apr_Bobcat_assembly_Adam     Bobcat  Entertainment/public assembly
2      2    Apr_Bobcat_assembly_Billy    Bobcat  Entertainment/public assembly
3      3    Apr_Bobcat_assembly_Camilla  Bobcat  Entertainment/public assembly
4      4    Apr_Bobcat_assembly_Franklin Bobcat  Entertainment/public assembly
5      5    Apr_Bobcat_education_Alissa  Bobcat  Education                    
6      6    Apr_Bobcat_education_Angela  Bobcat  Education                    
7      7    Apr_Bobcat_education_Barbra  Bobcat  Education                    
8      8    Apr_Bobcat_education_Coleman Bobcat  Education                    
9      9    Apr_Bobcat_education_Dylan   Bobcat  Education                    
10    10    Apr_Bobcat_education_Emile   Bobcat  Education                    
11    11    Apr_Bobcat_education_Hollis  Bobcat  Education                    
12    12    Apr_Bobcat_education_Jayne   Bobcat  Education                    
13    13    Apr_Bobcat_education_Karin   Bobcat  Education                    
14    14    Apr_Bobcat_education_Marisha Bobcat  Education                    
15    15    Apr_Bobcat_education_Miki    Bobcat  Education                    
16    16    Apr_Bobcat_education_Monte   Bobcat  Education                    
17    17    Apr_Bobcat_education_Rodrick Bobcat  Education                    
18    18    Apr_Bobcat_education_Rosalva Bobcat  Education                    
19    19    Apr_Bobcat_education_Toni    Bobcat  Education                    
20    20    Apr_Bobcat_education_Whitney Bobcat  Education                    
21    21    Apr_Bobcat_lodging_Darin     Bobcat  Lodging/residential          
22    22    Apr_Bobcat_lodging_Melaine   Bobcat  Lodging/residential          
23    23    Apr_Bobcat_lodging_Nickolas  Bobcat  Lodging/residential          
24    24    Apr_Bobcat_office_Alma       Bobcat  Office                       
25    25    Apr_Bobcat_office_Justine    Bobcat  Office                       
26    26    Apr_Bobcat_office_Kassandra  Bobcat  Office                       
27    27    Apr_Bobcat_office_Melody     Bobcat  Office                       
28    28    Apr_Bobcat_office_Nikita     Bobcat  Office                       
29    29    Apr_Bobcat_other_Howard      Bobcat  Other                        
30    30    Apr_Bobcat_other_Jovita      Bobcat  Other                        
...   ...   ...                          ...     ...                          
10243 10243 Sep_Peacock_office_Dara      Peacock Office                       
10244 10244 Sep_Peacock_office_Effie     Peacock Office                       
10245 10245 Sep_Peacock_office_Elton     Peacock Office                       
10246 10246 Sep_Peacock_office_Glenn     Peacock Office                       
10247 10247 Sep_Peacock_office_Jonathon  Peacock Office                       
10248 10248 Sep_Peacock_office_Julian    Peacock Office                       
10249 10249 Sep_Peacock_office_Major     Peacock Office                       
10250 10250 Sep_Peacock_office_Naomi     Peacock Office                       
10251 10251 Sep_Peacock_office_Norman    Peacock Office                       
10252 10252 Sep_Peacock_public_Kelvin    Peacock Public services              
10253 10253 Sep_Peacock_public_Linda     Peacock Public services              
10254 10254 Sep_Swan_unknown_Allison     Swan    miss                         
10255 10255 Sep_Swan_unknown_Andres      Swan    miss                         
10256 10256 Sep_Swan_unknown_Bette       Swan    miss                         
10257 10257 Sep_Swan_unknown_Christoper  Swan    miss                         
10258 10258 Sep_Swan_unknown_Douglas     Swan    miss                         
10259 10259 Sep_Swan_unknown_Esteban     Swan    miss                         
10260 10260 Sep_Swan_unknown_Fabian      Swan    miss                         
10261 10261 Sep_Swan_unknown_Ike         Swan    miss   

#### A.4.4 Droping the columns used to create the one hot encoding columns - the original string factorized and char columns

In [287]:
DF_BGP_OHC_Xnames<-DF_BGP_OHC_index[,!(names(DF_BGP_OHC_index) %in% c(strlst))]

In [288]:
DF_BGP_OHC_Xnames # DF_BGP_OHC the data frame witoun factors or characters and with one hot encoding

ID    sqm     lat     lng      El_Max_W1 El_Max_W2 El_Max_W3 El_Max_W4
1      1     2053.2 45.4215 -75.6972 147.2500  129.1300   171.0000 109.1300 
2      2    19859.1 45.4215 -75.6972 225.0000  202.0000   330.7500 219.5000 
3      3     3696.4 45.3876 -75.6960  30.6200   34.6300    37.3800  36.5000 
4      4    15047.4 45.4215 -75.6972 178.5000  180.0000   222.0000 324.0000 
5      5    11254.8 45.3876 -75.6960  95.5000  103.2500   160.0000 103.0000 
6      6     8802.7 45.4215 -75.6972 145.6200  139.1200   150.7500 184.1300 
7      7     2538.0 40.3500 -74.7000  65.3548    3.9608     9.6019  30.0058 
8      8    10551.9 45.4215 -75.6972 203.0000  217.0000   388.7500 208.0000 
9      9    17358.0 45.4215 -75.6972 227.2500  234.2500   355.5000 236.7500 
10    10     5003.3 45.3876 -75.6960  39.2499   34.5400    31.9096  32.8700 
11    11     8173.2 45.4215 -75.6972 204.0000  213.2500   329.0000 212.2500 
12    12     6259.5 45.4215 -75.6972 153.7500  157.7501   172.6301 144.2500 
13    13     6052.1 45.3876 -75.6960  76.2500   71.5700   104.3800  66.8800 
14    14     6913.8 45.4215 -75.6972 146.5010  133.0000   236.0000 125.2500 
15    15    16116.7 45.4215 -75.6972 149.1200  226.0000   228.3700 158.2500 
16    16     2147.2 45.3876 -75.6960  50.2500   58.3800    76.3800  48.8700 
17    17    11088.0 45.4215 -75.6972 115.1200  142.1301   175.0300 113.8700 
18    18     7836.0 45.4215 -75.6972 133.5000  141.3800   207.8800 134.6300 
19    19     2033.8 45.3876 -75.6960  45.8800   46.8800    49.3700  52.1200 
20    20     6957.1 45.4215 -75.6972 831.0000  782.0000  1062.0002 727.0000 
21    21     8220.1 45.3876 -75.6960 193.0000  275.5002   282.6000 228.5000 
22    22     3294.8 45.3876 -75.6960  50.5000   49.0000    79.0000  57.7500 
23    23     4834.1 45.4215 -75.6972  70.2500   72.0000    79.2500  64.7500 
24    24     1060.9 45.3876 -75.6960   7.0000    9.0000     8.0000  11.0000 
25    25     2445.7 40.3500 -74.7000  65.3548    3.9608     9.6019  30.0058 
26    26     4003.6 45.3876 -75.6960 120.6900  104.8700   117.6300 104.8800 
27    27     2503.6 40.3500 -74.7000  65.3548    3.9608     9.6019  30.0058 
28    28     3895.7 45.3876 -75.6960  55.5000   65.0000    96.7500  91.0000 
29    29      428.0 45.4215 -75.6972 511.0237  554.0771   747.0387 530.8704 
30    30      416.4 45.3876 -75.6960   5.0000   43.0000    82.0000  49.0000 
...   ...   ...     ...     ...      ...       ...       ...       ...      
10243 10243  4644.2 40.3500 -74.7000 247.3333  276.3333  317.2167  249.9333 
10244 10244  9723.9 40.3500 -74.7000 176.6333  174.2500  161.8333  170.1667 
10245 10245  9694.9 40.3500 -74.7000 193.0333  208.5833  224.8833  216.2000 
10246 10246  2179.3 40.3500 -74.7000  46.5983    3.9608    9.6019   17.0433 
10247 10247  3482.5 40.3500 -74.7000  46.5983    3.9608    9.6019   17.0433 
10248 10248  3913.9 40.3500 -74.7000  44.4667   45.4833   51.4500   52.0167 
10249 10249  6507.1 40.3500 -74.7000 234.5667  236.7000  241.7667  238.6167 
10250 10250  5072.2 40.3500 -74.7000  46.5983    3.9608    9.6019   17.0433 
10251 10251  3044.1 40.3500 -74.7000  44.8000   61.4167   71.3833   68.8500 
10252 10252 37324.1 40.3500 -74.7000 347.0167  331.0333  406.9333  411.1000 
10253 10253  3592.7 40.3500 -74.7000  46.5983    3.9608    9.6019   17.0433 
10254 10254  1699.8 30.2672 -97.7431 103.1610    5.1010    9.6019   30.0058 
10255 10255 11538.7 30.2672 -97.7431 103.1610    5.1010    9.6019   30.0058 
10256 10256  5777.3 30.2672 -97.7431 103.1610    5.1010    9.6019   30.0058 
10257 10257  8636.6 30.2672 -97.7431 103.1610    5.1010    9.6019   30.0058 
10258 10258  7736.2 30.2672 -97.7431 103.1610    5.1010    9.6019   30.0058 
10259 10259  6976.4 30.2672 -97.7431 103.1610    5.1010    9.6019   30.0058 
10260 10260  4233.6 30.2672 -97.7431 103.1610    5.1010    9.6019   30.0058 
10261 10261  6928.1 30.2672 -97.7431 103.1610    5.1010    9.6019   30.0058 
10262 10262 14806.3 30.2672 -97.7431 103.1610    5.1010    9.6019   30.0058 
10

In [289]:
write.csv(DF_BGP_OHC_Xnames, file="DF_BGP_OHC_Xnames_06062022.csv")

In [10]:
#DF_BGP_OHC_Xnames<-read.csv("DF_BGP_OHC_Xnames_06062022.csv")

### A.5. Transforming the numeric variables in to using log
#### A.5.1 Creating a new data frame to enable tarce back

In [290]:
DF_BGP_OHC_Xnames_log<-DF_BGP_OHC_Xnames

In [291]:
DF_BGP_OHC_Xnames_log[,'Min_dewTemperature_W4']<-abs(DF_BGP_OHC_Xnames_log[,'Min_dewTemperature_W4'])
# dealing with - values of dew temperatuer

#### A.5.2 Creating a numeric column list without the unrelevant columns: ID, sqm, lat, long

In [292]:
for(m in numlst) # getting the numbers of the columes for eazy use in the process.
    {
    print(paste(which(colnames(DF_BGP_OHC_Xnames)==m), m, sep=' : '))
    }

[1] "2 : sqm"
[1] "3 : lat"
[1] "4 : lng"
[1] "5 : El_Max_W1"
[1] "6 : El_Max_W2"
[1] "7 : El_Max_W3"
[1] "8 : El_Max_W4"
[1] "9 : El_Max_W5"
[1] "10 : El_Min_W1"
[1] "11 : El_Min_W2"
[1] "12 : El_Min_W3"
[1] "13 : El_Min_W4"
[1] "14 : El_Min_W5"
[1] "15 : El_AVG_W1"
[1] "16 : El_AVG_W2"
[1] "17 : El_AVG_W3"
[1] "18 : El_AVG_W4"
[1] "19 : El_AVG_W5"
[1] "20 : El_STD_W1"
[1] "21 : El_STD_W2"
[1] "22 : El_STD_W3"
[1] "23 : El_STD_W4"
[1] "24 : El_STD_W5"
[1] "25 : ChWt_Max_W1"
[1] "26 : ChWt_Max_W2"
[1] "27 : ChWt_Max_W3"
[1] "28 : ChWt_Max_W4"
[1] "29 : ChWt_Max_W5"
[1] "30 : ChWt_Min_W1"
[1] "31 : ChWt_Min_W2"
[1] "32 : ChWt_Min_W3"
[1] "33 : ChWt_Min_W4"
[1] "34 : ChWt_Min_W5"
[1] "35 : ChWt_AVG_W1"
[1] "36 : ChWt_AVG_W2"
[1] "37 : ChWt_AVG_W3"
[1] "38 : ChWt_AVG_W4"
[1] "39 : ChWt_AVG_W5"
[1] "40 : ChWt_STD_W1"
[1] "41 : ChWt_STD_W2"
[1] "42 : ChWt_STD_W3"
[1] "43 : ChWt_STD_W4"
[1] "44 : ChWt_STD_W5"
[1] "45 : MAX_airTemperature_W1"
[1] "46 : MAX_airTemperature_W2"
[1] "47 : MAX_air

In [16]:
numlst_log <- colnames(DF_BGP_OHC_Xnames[,c(5:45,85:94,145)])

In [26]:
numlst_log

[1] "lng"                   "El_Max_W1"             "El_Max_W2"            
 [4] "El_Max_W3"             "El_Max_W4"             "El_Max_W5"            
 [7] "El_Min_W1"             "El_Min_W2"             "El_Min_W3"            
[10] "El_Min_W4"             "El_Min_W5"             "El_AVG_W1"            
[13] "El_AVG_W2"             "El_AVG_W3"             "El_AVG_W4"            
[16] "El_AVG_W5"             "El_STD_W1"             "El_STD_W2"            
[19] "El_STD_W3"             "El_STD_W4"             "El_STD_W5"            
[22] "ChWt_Max_W1"           "ChWt_Max_W2"           "ChWt_Max_W3"          
[25] "ChWt_Max_W4"           "ChWt_Max_W5"           "ChWt_Min_W1"          
[28] "ChWt_Min_W2"           "ChWt_Min_W3"           "ChWt_Min_W4"          
[31] "ChWt_Min_W5"           "ChWt_AVG_W1"           "ChWt_AVG_W2"          
[34] "ChWt_AVG_W3"           "ChWt_AVG_W4"           "ChWt_AVG_W5"          
[37] "ChWt_STD_W1"           "ChWt_STD_W2"           "ChWt_STD_W3"          
[40] "ChWt_STD_W4"           "ChWt_STD_W5"           "Min_seaLvlPressure_W5"
[43] "Min_windDirection_W1"  "Min_windDirection_W2"  "Min_windDirection_W3" 
[46] "Min_windDirection_W4"  "Min_windDirection_W5"  "Min_windSpeed_W1"     
[49] "Min_windSpeed_W2"      "Min_windSpeed_W3"      "Min_windSpeed_W4"     
[52] "Std_windSpeed_W5"

In [17]:
length(numlst_log)

[1] 52

#### A.5.3 The log transformation of the relevant columns

In [296]:
DF_BGP_OHC_Xnames_log[,numlst_log]<-log(1+DF_BGP_OHC_Xnames_log[,numlst_log])

In [297]:
DF_BGP_OHC_Xnames_log # df_temp3_log is the transformed data frame with all meter columns transferd to log

ID    sqm     lat     lng      El_Max_W1 El_Max_W2 El_Max_W3 El_Max_W4
1      1     2053.2 45.4215 -75.6972 4.998900  4.868534  5.147494  4.701661 
2      2    19859.1 45.4215 -75.6972 5.420535  5.313206  5.804382  5.395898 
3      3     3696.4 45.3876 -75.6960 3.453790  3.573188  3.647536  3.624341 
4      4    15047.4 45.4215 -75.6972 5.190175  5.198497  5.407172  5.783825 
5      5    11254.8 45.3876 -75.6960 4.569543  4.646792  5.081404  4.644391 
6      6     8802.7 45.4215 -75.6972 4.987844  4.942499  5.022234  5.221058 
7      7     2538.0 40.3500 -74.7000 4.195016  1.601567  2.361033  3.434174 
8      8    10551.9 45.4215 -75.6972 5.318120  5.384495  5.965506  5.342334 
9      9    17358.0 45.4215 -75.6972 5.430442  5.460649  5.876334  5.471220 
10    10     5003.3 45.3876 -75.6960 3.695108  3.570659  3.493764  3.522530 
11    11     8173.2 45.4215 -75.6972 5.323010  5.367144  5.799093  5.362465 
12    12     6259.5 45.4215 -75.6972 5.041811  5.067331  5.156927  4.978456 
13    13     6052.1 45.3876 -75.6960 4.347047  4.284552  4.657573  4.217741 
14    14     6913.8 45.4215 -75.6972 4.993835  4.897840  5.468060  4.838264 
15    15    16116.7 45.4215 -75.6972 5.011435  5.424950  5.435336  5.070475 
16    16     2147.2 45.3876 -75.6960 3.936716  4.083957  4.348728  3.909420 
17    17    11088.0 45.4215 -75.6972 4.754624  4.963754  5.170654  4.743801 
18    18     7836.0 45.4215 -75.6972 4.901564  4.958500  5.341760  4.909931 
19    19     2033.8 45.3876 -75.6960 3.847591  3.868698  3.919396  3.972554 
20    20     6957.1 45.4215 -75.6972 6.723832  6.663133  6.968851  6.590301 
21    21     8220.1 45.3876 -75.6960 5.267858  5.622212  5.647565  5.435903 
22    22     3294.8 45.3876 -75.6960 3.941582  3.912023  4.382027  4.073291 
23    23     4834.1 45.4215 -75.6972 4.266195  4.290459  4.385147  4.185860 
24    24     1060.9 45.3876 -75.6960 2.079442  2.302585  2.197225  2.484907 
25    25     2445.7 40.3500 -74.7000 4.195016  1.601567  2.361033  3.434174 
26    26     4003.6 45.3876 -75.6960 4.801477  4.662212  4.776009  4.662306 
27    27     2503.6 40.3500 -74.7000 4.195016  1.601567  2.361033  3.434174 
28    28     3895.7 45.3876 -75.6960 4.034241  4.189655  4.582413  4.521789 
29    29      428.0 45.4215 -75.6972 6.238371  6.319107  6.617455  6.276400 
30    30      416.4 45.3876 -75.6960 1.791759  3.784190  4.418841  3.912023 
...   ...   ...     ...     ...      ...       ...       ...       ...      
10243 10243  4644.2 40.3500 -74.7000 5.514772  5.625220  5.762733  5.525187 
10244 10244  9723.9 40.3500 -74.7000 5.179721  5.166214  5.092727  5.142638 
10245 10245  9694.9 40.3500 -74.7000 5.268030  5.345121  5.420018  5.380819 
10246 10246  2179.3 40.3500 -74.7000 3.862797  1.601567  2.361033  2.892774 
10247 10247  3482.5 40.3500 -74.7000 3.862797  1.601567  2.361033  2.892774 
10248 10248  3913.9 40.3500 -74.7000 3.816980  3.839093  3.959860  3.970607 
10249 10249  6507.1 40.3500 -74.7000 5.461994  5.471009  5.492101  5.479041 
10250 10250  5072.2 40.3500 -74.7000 3.862797  1.601567  2.361033  2.892774 
10251 10251  3044.1 40.3500 -74.7000 3.824284  4.133833  4.281976  4.246350 
10252 10252 37324.1 40.3500 -74.7000 5.852250  5.805235  6.011104  6.021266 
10253 10253  3592.7 40.3500 -74.7000 3.862797  1.601567  2.361033  2.892774 
10254 10254  1699.8 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10255 10255 11538.7 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10256 10256  5777.3 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10257 10257  8636.6 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10258 10258  7736.2 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10259 10259  6976.4 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10260 10260  4233.6 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10261 10261  6928.1 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10262 10262 14806.3 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10

In [298]:
colnames(DF_BGP_OHC_Xnames_log)[199]<- 'SbPrUs.Ice.arena1' # changing one name arena and Arena

In [299]:
colnames(DF_BGP_OHC_Xnames_log)[209] <- 'SbPrUs.Office1' # changing one name office and Office

In [300]:
write.csv(DF_BGP_OHC_Xnames_log , file="DF_BGP_OHC_Xnames_log_06062022.csv")

In [302]:
DF_BGP_OHC_Xnames_log[,'Min_dewTemperature_W4']

In [303]:
summary(DF_BGP_OHC_Xnames_log)

       ID             sqm               lat             lng         
 Min.   :    1   Min.   :   26.3   Min.   :28.52   Min.   :-111.93  
 1st Qu.: 2569   1st Qu.: 3446.6   1st Qu.:30.27   1st Qu.: -97.74  
 Median : 5136   Median : 6929.8   Median :40.35   Median : -93.26  
 Mean   : 5136   Mean   :10196.6   Mean   :37.46   Mean   : -89.96  
 3rd Qu.: 7704   3rd Qu.:13020.9   3rd Qu.:44.98   3rd Qu.: -76.49  
 Max.   :10272   Max.   :80038.2   Max.   :45.42   Max.   : -74.70  
   El_Max_W1           El_Max_W2        El_Max_W3         El_Max_W4      
 Min.   : 0.002796   Min.   :0.0198   Min.   : 0.0198   Min.   : 0.0198  
 1st Qu.: 4.147692   1st Qu.:3.7944   1st Qu.: 3.8122   1st Qu.: 3.8546  
 Median : 4.826171   Median :4.7597   Median : 4.7536   Median : 4.8111  
 Mean   : 4.824857   Mean   :4.5808   Mean   : 4.6378   Mean   : 4.7447  
 3rd Qu.: 5.556182   3rd Qu.:5.5608   3rd Qu.: 5.5423   3rd Qu.: 5.5545  
 Max.   :10.699585   Max.   :9.8788   Max.   :10.3711   Max.   :11.2869  

In [305]:
dbWriteTable(conn,"DF_BGP_OHC_log",DF_BGP_OHC_Xnames_log)

In [17]:
#DF_BGP_OHC_Xnames_log <- dbGetQuery(conn, "SELECT * FROM DF_BGP_OHC_log")

In [20]:
write.csv(DF_BGP_OHC_Xnames_log, file="DF_BGP_OHC_log_07062022.csv")

In [12]:
#DF_BGP_OHC_Xnames_log<-read.csv("DF_BGP_OHC_log_07062022.csv")

## B. Investigating the changes due to the Feature Engeneering 
### B.1 Using "mechkar" to create the table1 summary

In [13]:
df <- DF_BGP_OHC_Xnames_log # for easy use

In [19]:
source("mechkar.r")

#### B.1.1 Creating the statistics summary tables.

In [308]:
tab1 <- Table1(data=df[,1:ncol(df)],y="El_Nxt_Mnth_Avg_OC")  #with the outcome

  |======================================================================| 100%

The dependent variable has more than 8 levels, table too large!



In [309]:
tab2 <- Table1(data=df[,1:ncol(df)-1],y="El_Nxt_Mnth_Avg_OC")  # without the outcome

  |======================================================================| 100%

The dependent variable has more than 8 levels, table too large!



In [310]:
tab2

Variables                    p-value                   
1    Variables       Categories   Population                
2    Individuals     n            10272                     
3    ID              Mean (SD)    5,136.5 (2,965.4)         
4    ID              Median (IQR) 5,136.5 (2,568.8-7,704.2) 
5    ID              Missing (%)   --                       
6    sqm             Mean (SD)    10,196.7 (10,772.2)       
7    sqm             Median (IQR) 6,929.8 (3,446.6-13,020.9)
8    sqm             Missing (%)   --                       
9    lat             Mean (SD)    37.5 (6.5)                
10   lat             Median (IQR) 40.3 (30.3-45.0)          
11   lat             Missing (%)   --                       
12   lng             Mean (SD)    -90.0 (12.9)              
13   lng             Median (IQR) -93.3 (-97.7--76.5)       
14   lng             Missing (%)   --                       
15   El_Max_W1       Mean (SD)    4.8 (1.2)                 
16   El_Max_W1       Median (IQR) 4.8 (4.1-5.6)             
17   El_Max_W1       Missing (%)   --                       
18   El_Max_W2       Mean (SD)    4.6 (1.5)                 
19   El_Max_W2       Median (IQR) 4.8 (3.8-5.6)             
20   El_Max_W2       Missing (%)   --                       
21   El_Max_W3       Mean (SD)    4.6 (1.3)                 
22   El_Max_W3       Median (IQR) 4.8 (3.8-5.5)             
23   El_Max_W3       Missing (%)   --                       
24   El_Max_W4       Mean (SD)    4.7 (1.2)                 
25   El_Max_W4       Median (IQR) 4.8 (3.9-5.6)             
26   El_Max_W4       Missing (%)   --                       
27   El_Max_W5       Mean (SD)    4.7 (1.3)                 
28   El_Max_W5       Median (IQR) 4.8 (3.8-5.6)             
29   El_Max_W5       Missing (%)   --                       
30   El_Min_W1       Mean (SD)    3.9 (1.4)                 
...  ...             ...          ...                       
1419 Stm_STD_W3.low  Mean (SD)    0.1 (0.3)                 
1420 Stm_STD_W3.low  Median (IQR) 0.0 (0.0-0.0)             
1421 Stm_STD_W3.low  Missing (%)   --                       
1422 Stm_STD_W3.mid  Mean (SD)    0.2 (0.4)                 
1423 Stm_STD_W3.mid  Median (IQR) 0.0 (0.0-0.0)             
1424 Stm_STD_W3.mid  Missing (%)   --                       
1425 Stm_STD_W3.miss Mean (SD)    0.6 (0.5)                 
1426 Stm_STD_W3.miss Median (IQR) 1.0 (0.0-1.0)             
1427 Stm_STD_W3.miss Missing (%)   --                       
1428 Stm_STD_W4.high Mean (SD)    0.1 (0.3)                 
1429 Stm_STD_W4.high Median (IQR) 0.0 (0.0-0.0)             
1430 Stm_STD_W4.high Missing (%)   --                       
1431 Stm_STD_W4.low  Mean (SD)    0.1 (0.3)                 
1432 Stm_STD_W4.low  Median (IQR) 0.0 (0.0-0.0)             
1433 Stm_STD_W4.low  Missing (%)   --                       
1434 Stm_STD_W4.mid  Mean (SD)    0.2 (0.4)                 
1435 Stm_STD_W4.mid  Median (IQR) 0.0 (0.0-0.0)             
1436 Stm_STD_W4.mid  Missing (%)   --                       
1437 Stm_STD_W4.miss Mean (SD)    0.6 (0.5)                 
1438 Stm_STD_W4.miss Median (IQR) 1.0 (0.0-1.0)             
1439 Stm_STD_W4.miss Missing (%)   --                       
1440 Stm_STD_W5.high Mean (SD)    0.1 (0.3)                 
1441 Stm_STD_W5.high Median (IQR) 0.0 (0.0-0.0)             
1442 Stm_STD_W5.high Missing (%)   --                       
1443 Stm_STD_W5.low  Mean (SD)    0.1 (0.3)                 
1444 Stm_STD_W5.low  Median (IQR) 0.0 (0.0-0.0)             
1445 Stm_STD_W5.low  Missing (%)   --                       
1446 Stm_STD_W5.mid  Mean (SD)    0.2 (0.4)                 
1447 Stm_STD_W5.mid  Median (IQR) 0.0 (0.0-0.0)             
1448 Stm_STD_W5.mid  Missing (%)   --

In [311]:
write.csv(tab2, file="DF_BGP_OHC_Xnames_log_sum_06062022_mechkar.csv")

In [312]:
tab1

Variables                    p-value                   
1    Variables       Categories   Population                
2    Individuals     n            10272                     
3    ID              Mean (SD)    5,136.5 (2,965.4)         
4    ID              Median (IQR) 5,136.5 (2,568.8-7,704.2) 
5    ID              Missing (%)   --                       
6    sqm             Mean (SD)    10,196.7 (10,772.2)       
7    sqm             Median (IQR) 6,929.8 (3,446.6-13,020.9)
8    sqm             Missing (%)   --                       
9    lat             Mean (SD)    37.5 (6.5)                
10   lat             Median (IQR) 40.3 (30.3-45.0)          
11   lat             Missing (%)   --                       
12   lng             Mean (SD)    -90.0 (12.9)              
13   lng             Median (IQR) -93.3 (-97.7--76.5)       
14   lng             Missing (%)   --                       
15   El_Max_W1       Mean (SD)    4.8 (1.2)                 
16   El_Max_W1       Median (IQR) 4.8 (4.1-5.6)             
17   El_Max_W1       Missing (%)   --                       
18   El_Max_W2       Mean (SD)    4.6 (1.5)                 
19   El_Max_W2       Median (IQR) 4.8 (3.8-5.6)             
20   El_Max_W2       Missing (%)   --                       
21   El_Max_W3       Mean (SD)    4.6 (1.3)                 
22   El_Max_W3       Median (IQR) 4.8 (3.8-5.5)             
23   El_Max_W3       Missing (%)   --                       
24   El_Max_W4       Mean (SD)    4.7 (1.2)                 
25   El_Max_W4       Median (IQR) 4.8 (3.9-5.6)             
26   El_Max_W4       Missing (%)   --                       
27   El_Max_W5       Mean (SD)    4.7 (1.3)                 
28   El_Max_W5       Median (IQR) 4.8 (3.8-5.6)             
29   El_Max_W5       Missing (%)   --                       
30   El_Min_W1       Mean (SD)    3.9 (1.4)                 
...  ...             ...          ...                       
1422 Stm_STD_W3.mid  Mean (SD)    0.2 (0.4)                 
1423 Stm_STD_W3.mid  Median (IQR) 0.0 (0.0-0.0)             
1424 Stm_STD_W3.mid  Missing (%)   --                       
1425 Stm_STD_W3.miss Mean (SD)    0.6 (0.5)                 
1426 Stm_STD_W3.miss Median (IQR) 1.0 (0.0-1.0)             
1427 Stm_STD_W3.miss Missing (%)   --                       
1428 Stm_STD_W4.high Mean (SD)    0.1 (0.3)                 
1429 Stm_STD_W4.high Median (IQR) 0.0 (0.0-0.0)             
1430 Stm_STD_W4.high Missing (%)   --                       
1431 Stm_STD_W4.low  Mean (SD)    0.1 (0.3)                 
1432 Stm_STD_W4.low  Median (IQR) 0.0 (0.0-0.0)             
1433 Stm_STD_W4.low  Missing (%)   --                       
1434 Stm_STD_W4.mid  Mean (SD)    0.2 (0.4)                 
1435 Stm_STD_W4.mid  Median (IQR) 0.0 (0.0-0.0)             
1436 Stm_STD_W4.mid  Missing (%)   --                       
1437 Stm_STD_W4.miss Mean (SD)    0.6 (0.5)                 
1438 Stm_STD_W4.miss Median (IQR) 1.0 (0.0-1.0)             
1439 Stm_STD_W4.miss Missing (%)   --                       
1440 Stm_STD_W5.high Mean (SD)    0.1 (0.3)                 
1441 Stm_STD_W5.high Median (IQR) 0.0 (0.0-0.0)             
1442 Stm_STD_W5.high Missing (%)   --                       
1443 Stm_STD_W5.low  Mean (SD)    0.1 (0.3)                 
1444 Stm_STD_W5.low  Median (IQR) 0.0 (0.0-0.0)             
1445 Stm_STD_W5.low  Missing (%)   --                       
1446 Stm_STD_W5.mid  Mean (SD)    0.2 (0.4)                 
1447 Stm_STD_W5.mid  Median (IQR) 0.0 (0.0-0.0)             
1448 Stm_STD_W5.mid  Missing (%)   --                       
1449 Stm_STD_W5.miss Mean (SD)    0.6 (0.5)                 
1450 Stm_STD_W5.miss Median (IQR) 1.0 (0.0-1.0)             
1451 Stm_STD_W5.miss Missing (%)   --

In [313]:
summary (tab1)

  Variables                              p-value         
 Length:1451        Length:1451        Length:1451       
 Class :character   Class :character   Class :character  
 Mode  :character   Mode  :character   Mode  :character  

In [314]:
summary (tab2)

  Variables                              p-value         
 Length:1448        Length:1448        Length:1448       
 Class :character   Class :character   Class :character  
 Mode  :character   Mode  :character   Mode  :character  

In [315]:
tab1[tab1$Variables == "El_Nxt_Mnth_Avg_OC",]

Variables                       p-value      
435 El_Nxt_Mnth_Avg_OC Mean (SD)    4.3 (1.3)    
436 El_Nxt_Mnth_Avg_OC Median (IQR) 4.4 (3.4-5.2)
437 El_Nxt_Mnth_Avg_OC Missing (%)   --

In [316]:
tab1[is.na(tab1$'p-value')==F,]

Variables                    p-value                   
1    Variables       Categories   Population                
2    Individuals     n            10272                     
3    ID              Mean (SD)    5,136.5 (2,965.4)         
4    ID              Median (IQR) 5,136.5 (2,568.8-7,704.2) 
5    ID              Missing (%)   --                       
6    sqm             Mean (SD)    10,196.7 (10,772.2)       
7    sqm             Median (IQR) 6,929.8 (3,446.6-13,020.9)
8    sqm             Missing (%)   --                       
9    lat             Mean (SD)    37.5 (6.5)                
10   lat             Median (IQR) 40.3 (30.3-45.0)          
11   lat             Missing (%)   --                       
12   lng             Mean (SD)    -90.0 (12.9)              
13   lng             Median (IQR) -93.3 (-97.7--76.5)       
14   lng             Missing (%)   --                       
15   El_Max_W1       Mean (SD)    4.8 (1.2)                 
16   El_Max_W1       Median (IQR) 4.8 (4.1-5.6)             
17   El_Max_W1       Missing (%)   --                       
18   El_Max_W2       Mean (SD)    4.6 (1.5)                 
19   El_Max_W2       Median (IQR) 4.8 (3.8-5.6)             
20   El_Max_W2       Missing (%)   --                       
21   El_Max_W3       Mean (SD)    4.6 (1.3)                 
22   El_Max_W3       Median (IQR) 4.8 (3.8-5.5)             
23   El_Max_W3       Missing (%)   --                       
24   El_Max_W4       Mean (SD)    4.7 (1.2)                 
25   El_Max_W4       Median (IQR) 4.8 (3.9-5.6)             
26   El_Max_W4       Missing (%)   --                       
27   El_Max_W5       Mean (SD)    4.7 (1.3)                 
28   El_Max_W5       Median (IQR) 4.8 (3.8-5.6)             
29   El_Max_W5       Missing (%)   --                       
30   El_Min_W1       Mean (SD)    3.9 (1.4)                 
...  ...             ...          ...                       
1422 Stm_STD_W3.mid  Mean (SD)    0.2 (0.4)                 
1423 Stm_STD_W3.mid  Median (IQR) 0.0 (0.0-0.0)             
1424 Stm_STD_W3.mid  Missing (%)   --                       
1425 Stm_STD_W3.miss Mean (SD)    0.6 (0.5)                 
1426 Stm_STD_W3.miss Median (IQR) 1.0 (0.0-1.0)             
1427 Stm_STD_W3.miss Missing (%)   --                       
1428 Stm_STD_W4.high Mean (SD)    0.1 (0.3)                 
1429 Stm_STD_W4.high Median (IQR) 0.0 (0.0-0.0)             
1430 Stm_STD_W4.high Missing (%)   --                       
1431 Stm_STD_W4.low  Mean (SD)    0.1 (0.3)                 
1432 Stm_STD_W4.low  Median (IQR) 0.0 (0.0-0.0)             
1433 Stm_STD_W4.low  Missing (%)   --                       
1434 Stm_STD_W4.mid  Mean (SD)    0.2 (0.4)                 
1435 Stm_STD_W4.mid  Median (IQR) 0.0 (0.0-0.0)             
1436 Stm_STD_W4.mid  Missing (%)   --                       
1437 Stm_STD_W4.miss Mean (SD)    0.6 (0.5)                 
1438 Stm_STD_W4.miss Median (IQR) 1.0 (0.0-1.0)             
1439 Stm_STD_W4.miss Missing (%)   --                       
1440 Stm_STD_W5.high Mean (SD)    0.1 (0.3)                 
1441 Stm_STD_W5.high Median (IQR) 0.0 (0.0-0.0)             
1442 Stm_STD_W5.high Missing (%)   --                       
1443 Stm_STD_W5.low  Mean (SD)    0.1 (0.3)                 
1444 Stm_STD_W5.low  Median (IQR) 0.0 (0.0-0.0)             
1445 Stm_STD_W5.low  Missing (%)   --                       
1446 Stm_STD_W5.mid  Mean (SD)    0.2 (0.4)                 
1447 Stm_STD_W5.mid  Median (IQR) 0.0 (0.0-0.0)             
1448 Stm_STD_W5.mid  Missing (%)   --                       
1449 Stm_STD_W5.miss Mean (SD)    0.6 (0.5)                 
1450 Stm_STD_W5.miss Median (IQR) 1.0 (0.0-1.0)             
1451 Stm_STD_W5.miss Missing (%)   --

In [317]:
write.csv(tab1[is.na(tab1$'p-value')==F,], file="BGP_OHC_log_nas_mechkar060062022.csv")

In [318]:
nm <- names(df)
nm

[1] "ID"                                 "sqm"                               
  [3] "lat"                                "lng"                               
  [5] "El_Max_W1"                          "El_Max_W2"                         
  [7] "El_Max_W3"                          "El_Max_W4"                         
  [9] "El_Max_W5"                          "El_Min_W1"                         
 [11] "El_Min_W2"                          "El_Min_W3"                         
 [13] "El_Min_W4"                          "El_Min_W5"                         
 [15] "El_AVG_W1"                          "El_AVG_W2"                         
 [17] "El_AVG_W3"                          "El_AVG_W4"                         
 [19] "El_AVG_W5"                          "El_STD_W1"                         
 [21] "El_STD_W2"                          "El_STD_W3"                         
 [23] "El_STD_W4"                          "El_STD_W5"                         
 [25] "ChWt_Max_W1"                        "ChWt_Max_W2"                       
 [27] "ChWt_Max_W3"                        "ChWt_Max_W4"                       
 [29] "ChWt_Max_W5"                        "ChWt_Min_W1"                       
 [31] "ChWt_Min_W2"                        "ChWt_Min_W3"                       
 [33] "ChWt_Min_W4"                        "ChWt_Min_W5"                       
 [35] "ChWt_AVG_W1"                        "ChWt_AVG_W2"                       
 [37] "ChWt_AVG_W3"                        "ChWt_AVG_W4"                       
 [39] "ChWt_AVG_W5"                        "ChWt_STD_W1"                       
 [41] "ChWt_STD_W2"                        "ChWt_STD_W3"                       
 [43] "ChWt_STD_W4"                        "ChWt_STD_W5"                       
 [45] "MAX_airTemperature_W1"              "MAX_airTemperature_W2"             
 [47] "MAX_airTemperature_W3"              "MAX_airTemperature_W4"             
 [49] "MAX_airTemperature_W5"              "MAX_dewTemperature_W1"             
 [51] "MAX_dewTemperature_W2"              "MAX_dewTemperature_W3"             
 [53] "MAX_dewTemperature_W4"              "MAX_dewTemperature_W5"             
 [55] "MAX_seaLvlPressure_W1"              "MAX_seaLvlPressure_W2"             
 [57] "MAX_seaLvlPressure_W3"              "MAX_seaLvlPressure_W4"             
 [59] "MAX_seaLvlPressure_W5"              "MAX_windDirection_W1"              
 [61] "MAX_windDirection_W2"               "MAX_windDirection_W3"              
 [63] "MAX_windDirection_W4"               "MAX_windDirection_W5"              
 [65] "MAX_windSpeed_W1"                   "MAX_windSpeed_W2"                  
 [67] "MAX_windSpeed_W3"                   "MAX_windSpeed_W4"                  
 [69] "MAX_windSpeed_W5"                   "Min_airTemperature_W1"             
 [71] "Min_airTemperature_W2"              "Min_airTemperature_W3"             
 [73] "Min_airTemperature_W4"              "Min_airTemperature_W5"             
 [75] "Min_dewTemperature_W1"              "Min_dewTemperature_W2"             
 [77] "Min_dewTemperature_W3"              "Min_dewTemperature_W4"             
 [79] "Min_dewTemperature_W5"              "Min_seaLvlPressure_W1"             
 [81] "Min_seaLvlPressure_W2"              "Min_seaLvlPressure_W3"             
 [83] "Min_seaLvlPressure_W4"              "Min_seaLvlPressure_W5"             
 [85] "Min_windDirection_W1"               "Min_windDirection_W2"              
 [87] "Min_windDirection_W3"               "Min_windDirection_W4"              
 [89] "Min_windDirection_W5"               "Min_windSpeed_W1"                  
 [91] "Min_windSpeed_W2"                   "Min_windSpeed_W3"                  
 [93] "Min_windSpeed_W4"                   "Min_windSpeed_W5"                  
 [95] "Avg_airTemperature_W1"              "Avg_airTemperature_W2"             
 [97] "Avg_airTemperature_W3"              "Avg_airTemperature_W4"             
 [99] "Avg_airTemperature_W5"              "Avg_dewTemperature_W1"             
[1

In [319]:
length(nm)

[1] 483

In [320]:
for (n in nm [1:length(nm)-1])
    {
        print(n)
        print(tab1[tab1$Variables == n,])
    }

[1] "ID"
  Variables                                p-value
3        ID    Mean (SD)         5,136.5 (2,965.4)
4        ID Median (IQR) 5,136.5 (2,568.8-7,704.2)
5        ID  Missing (%)                       -- 
[1] "sqm"
  Variables                                 p-value
6       sqm    Mean (SD)        10,196.7 (10,772.2)
7       sqm Median (IQR) 6,929.8 (3,446.6-13,020.9)
8       sqm  Missing (%)                        -- 
[1] "lat"
   Variables                       p-value
9        lat    Mean (SD)       37.5 (6.5)
10       lat Median (IQR) 40.3 (30.3-45.0)
11       lat  Missing (%)              -- 
[1] "lng"
   Variables                          p-value
12       lng    Mean (SD)        -90.0 (12.9)
13       lng Median (IQR) -93.3 (-97.7--76.5)
14       lng  Missing (%)                 -- 
[1] "El_Max_W1"
   Variables                    p-value
15 El_Max_W1    Mean (SD)     4.8 (1.2)
16 El_Max_W1 Median (IQR) 4.8 (4.1-5.6)
17 El_Max_W1  Missing (%)           -- 
[1] "El_Max_W2"
 

#### B.1.2 Distribution of variables and Relationship with the outcome - creating the report

In [30]:
#install.packages("mechkar")

In [325]:
exploreData(data=df, y="El_Nxt_Mnth_Avg_OC", dir='./report06062022')

  |                                                                      |   0%

`geom_smooth()` using formula 'y ~ x'



  |                                                                      |   0%

`geom_smooth()` using formula 'y ~ x'



  |                                                                      |   0%

...

`geom_smooth()` using formula 'y ~ x'



  |                                                                      |   0%

`geom_smooth()` using formula 'y ~ x'



  |======================================================================| 100%

ERROR: Error in shell.exec(url): './report06062022/report.html' not found


## B.2. Usign 'dlookr' library to better view of statistics summary

In [158]:
#install.packages('dlookr')   # 'Nofar' way - more convenient way to look at the statistics summary

In [138]:
#library(dlookr)

In [321]:
df_num_diag <- diagnose_numeric(df) # only numeric
df_num_diag

variables       min           Q1          mean         median     
1   ID               1.000000e+00 2568.750000  5136.500000 5136.500000
2   sqm              2.630000e+01 3446.600000 10196.651986 6929.800000
3   lat              2.851769e+01   30.267200    37.457850   40.350000
4   lng             -1.119281e+02  -97.743100   -89.955171  -93.255398
5   El_Max_W1        2.796087e-03    4.147692     4.824857    4.826171
6   El_Max_W2        1.980263e-02    3.794364     4.580839    4.759714
7   El_Max_W3        1.980263e-02    3.812166     4.637771    4.753590
8   El_Max_W4        1.980263e-02    3.854582     4.744718    4.811147
9   El_Max_W5        2.796087e-03    3.806662     4.680672    4.792326
10  El_Min_W1        2.796087e-03    3.115624     3.943122    4.103825
11  El_Min_W2        2.796087e-03    2.734549     3.727493    3.793672
12  El_Min_W3        2.796087e-03    2.732541     3.774851    3.778492
13  El_Min_W4        2.796087e-03    3.087048     3.881227    3.824721
14  El_Min_W5        2.796087e-03    2.708050     3.814546    3.806662
15  El_AVG_W1        2.796087e-03    3.713376     4.435693    4.430419
16  El_AVG_W2        1.980263e-02    3.294727     4.195430    4.314401
17  El_AVG_W3        1.980263e-02    3.324143     4.265971    4.332307
18  El_AVG_W4        1.980263e-02    3.434174     4.350658    4.336141
19  El_AVG_W5        2.796087e-03    3.329926     4.289606    4.357507
20  El_STD_W1        0.000000e+00    2.241970     3.155421    3.115611
21  El_STD_W2        0.000000e+00    1.928816     2.745449    2.800213
22  El_STD_W3        0.000000e+00    2.066691     2.839796    2.856045
23  El_STD_W4        0.000000e+00    2.063944     2.851125    2.873988
24  El_STD_W5        0.000000e+00    1.983535     2.803708    2.876944
25  ChWt_Max_W1      0.000000e+00    5.027569     6.408929    6.558648
26  ChWt_Max_W2      0.000000e+00    5.021102     6.364416    6.546868
27  ChWt_Max_W3      0.000000e+00    5.063080     6.427384    6.590293
28  ChWt_Max_W4      0.000000e+00    5.156665     6.455372    6.600575
29  ChWt_Max_W5      0.000000e+00    4.889513     6.325745    6.521755
30  ChWt_Min_W1      0.000000e+00    0.000000     3.020012    2.418072
... ...             ...           ...         ...          ...        
454 Stm_AVG_W3.mid  0             0           0.17552570   0          
455 Stm_AVG_W3.miss 0             0           0.64398364   1          
456 Stm_AVG_W4.high 0             0           0.08907710   0          
457 Stm_AVG_W4.low  0             0           0.09151090   0          
458 Stm_AVG_W4.mid  0             0           0.17552570   0          
459 Stm_AVG_W4.miss 0             0           0.64388629   1          
460 Stm_AVG_W5.high 0             0           0.09063474   0          
461 Stm_AVG_W5.low  0             0           0.09326324   0          
462 Stm_AVG_W5.mid  0             0           0.17844626   0          
463 Stm_AVG_W5.miss 0             0           0.63765576   1          
464 Stm_STD_W1.high 0             0           0.09034268   0          
465 Stm_STD_W1.low  0             0           0.09647586   0          
466 Stm_STD_W1.mid  0             0           0.17435748   0          
467 Stm_STD_W1.miss 0             0           0.63882399   1          
468 Stm_STD_W2.high 0             0           0.09034268   0          
469 Stm_STD_W2.low  0             0           0.09754673   0          
470 Stm_STD_W2.mid  0             0           0.17338396   0          
471 Stm_STD_W2.miss 0             0           0.63872664   1          
472 Stm_STD_W3.high 0             0           0.08897975   0          
473 Stm_STD_W3.low  0             0           0.09579439   0          
474 Stm_STD_W3.mid  0             0           0.17114486   0          
475 Stm_STD_W3.miss 0             0           0.64408100   1          
476 Stm_STD_W4.high 0             0           0.08907710   0          
477 Stm_STD_W4.low  0             0           0.09511293   0          
478 Stm_STD_W4.mid  0       

In [322]:
df_diag <- diagnose(df) # all data - different view
df_diag

variables       types   missing_count missing_percent unique_count
1   ID              numeric 0             0               10272       
2   sqm             numeric 0             0                 832       
3   lat             numeric 0             0                   8       
4   lng             numeric 0             0                   8       
5   El_Max_W1       numeric 0             0                7452       
6   El_Max_W2       numeric 0             0                7339       
7   El_Max_W3       numeric 0             0                7258       
8   El_Max_W4       numeric 0             0                7293       
9   El_Max_W5       numeric 0             0                7456       
10  El_Min_W1       numeric 0             0                6734       
11  El_Min_W2       numeric 0             0                6639       
12  El_Min_W3       numeric 0             0                6597       
13  El_Min_W4       numeric 0             0                6660       
14  El_Min_W5       numeric 0             0                6732       
15  El_AVG_W1       numeric 0             0                9066       
16  El_AVG_W2       numeric 0             0                8973       
17  El_AVG_W3       numeric 0             0                8942       
18  El_AVG_W4       numeric 0             0                8963       
19  El_AVG_W5       numeric 0             0                9078       
20  El_STD_W1       numeric 0             0                8968       
21  El_STD_W2       numeric 0             0                8955       
22  El_STD_W3       numeric 0             0                8924       
23  El_STD_W4       numeric 0             0                8954       
24  El_STD_W5       numeric 0             0                9061       
25  ChWt_Max_W1     numeric 0             0                5005       
26  ChWt_Max_W2     numeric 0             0                4945       
27  ChWt_Max_W3     numeric 0             0                4943       
28  ChWt_Max_W4     numeric 0             0                4970       
29  ChWt_Max_W5     numeric 0             0                5016       
30  ChWt_Min_W1     numeric 0             0                3081       
... ...             ...     ...           ...             ...         
454 Stm_AVG_W3.mid  numeric 0             0               2           
455 Stm_AVG_W3.miss numeric 0             0               2           
456 Stm_AVG_W4.high numeric 0             0               2           
457 Stm_AVG_W4.low  numeric 0             0               2           
458 Stm_AVG_W4.mid  numeric 0             0               2           
459 Stm_AVG_W4.miss numeric 0             0               2           
460 Stm_AVG_W5.high numeric 0             0               2           
461 Stm_AVG_W5.low  numeric 0             0               2           
462 Stm_AVG_W5.mid  numeric 0             0               2           
463 Stm_AVG_W5.miss numeric 0             0               2           
464 Stm_STD_W1.high numeric 0             0               2           
465 Stm_STD_W1.low  numeric 0             0               2           
466 Stm_STD_W1.mid  numeric 0             0               2           
467 Stm_STD_W1.miss numeric 0             0               2           
468 Stm_STD_W2.high numeric 0             0               2           
469 Stm_STD_W2.low  numeric 0             0               2           
470 Stm_STD_W2.mid  numeric 0             0               2           
471 Stm_STD_W2.miss numeric 0             0               2           
472 Stm_STD_W3.high numeric 0             0               2           
473 Stm_STD_W3.low  numeric 0             0               2           
474 Stm_STD_W3.mid  numeric 0             0               2           
475 Stm_STD_W3.miss numeric 0             0               2           
476 Stm_STD_W4.high numeric 0             0               2           
477 Stm_STD_W4.low  numeric 0             0               2           
478 Stm_STD_W4.mid  numeric 

In [323]:
write.csv(df_num_diag, file="BGP_OHC_log_diag-06062022.csv")

In [324]:
write.csv(df_diag, file="BGP_OHC_log_diag_short_06062022.csv")

## C. Checkin for correlations -  as we have parametirc (continuece) outcome

In [31]:
df

ID    sqm     lat     lng      El_Max_W1 El_Max_W2 El_Max_W3 El_Max_W4
1      1     2053.2 45.4215 -75.6972 4.998900  4.868534  5.147494  4.701661 
2      2    19859.1 45.4215 -75.6972 5.420535  5.313206  5.804382  5.395898 
3      3     3696.4 45.3876 -75.6960 3.453790  3.573188  3.647536  3.624341 
4      4    15047.4 45.4215 -75.6972 5.190175  5.198497  5.407172  5.783825 
5      5    11254.8 45.3876 -75.6960 4.569543  4.646792  5.081404  4.644391 
6      6     8802.7 45.4215 -75.6972 4.987844  4.942499  5.022234  5.221058 
7      7     2538.0 40.3500 -74.7000 4.195016  1.601567  2.361033  3.434174 
8      8    10551.9 45.4215 -75.6972 5.318120  5.384495  5.965506  5.342334 
9      9    17358.0 45.4215 -75.6972 5.430442  5.460649  5.876334  5.471220 
10    10     5003.3 45.3876 -75.6960 3.695108  3.570659  3.493764  3.522530 
11    11     8173.2 45.4215 -75.6972 5.323010  5.367144  5.799093  5.362465 
12    12     6259.5 45.4215 -75.6972 5.041811  5.067331  5.156927  4.978456 
13    13     6052.1 45.3876 -75.6960 4.347047  4.284552  4.657573  4.217741 
14    14     6913.8 45.4215 -75.6972 4.993835  4.897840  5.468060  4.838264 
15    15    16116.7 45.4215 -75.6972 5.011435  5.424950  5.435336  5.070475 
16    16     2147.2 45.3876 -75.6960 3.936716  4.083957  4.348728  3.909420 
17    17    11088.0 45.4215 -75.6972 4.754624  4.963754  5.170654  4.743801 
18    18     7836.0 45.4215 -75.6972 4.901564  4.958500  5.341760  4.909931 
19    19     2033.8 45.3876 -75.6960 3.847591  3.868698  3.919396  3.972554 
20    20     6957.1 45.4215 -75.6972 6.723832  6.663133  6.968851  6.590301 
21    21     8220.1 45.3876 -75.6960 5.267858  5.622212  5.647565  5.435903 
22    22     3294.8 45.3876 -75.6960 3.941582  3.912023  4.382027  4.073291 
23    23     4834.1 45.4215 -75.6972 4.266195  4.290459  4.385147  4.185860 
24    24     1060.9 45.3876 -75.6960 2.079442  2.302585  2.197225  2.484907 
25    25     2445.7 40.3500 -74.7000 4.195016  1.601567  2.361033  3.434174 
26    26     4003.6 45.3876 -75.6960 4.801477  4.662212  4.776009  4.662306 
27    27     2503.6 40.3500 -74.7000 4.195016  1.601567  2.361033  3.434174 
28    28     3895.7 45.3876 -75.6960 4.034241  4.189655  4.582413  4.521789 
29    29      428.0 45.4215 -75.6972 6.238371  6.319107  6.617455  6.276400 
30    30      416.4 45.3876 -75.6960 1.791759  3.784190  4.418841  3.912023 
...   ...   ...     ...     ...      ...       ...       ...       ...      
10243 10243  4644.2 40.3500 -74.7000 5.514772  5.625220  5.762733  5.525187 
10244 10244  9723.9 40.3500 -74.7000 5.179721  5.166214  5.092727  5.142638 
10245 10245  9694.9 40.3500 -74.7000 5.268030  5.345121  5.420018  5.380819 
10246 10246  2179.3 40.3500 -74.7000 3.862797  1.601567  2.361033  2.892774 
10247 10247  3482.5 40.3500 -74.7000 3.862797  1.601567  2.361033  2.892774 
10248 10248  3913.9 40.3500 -74.7000 3.816980  3.839093  3.959860  3.970607 
10249 10249  6507.1 40.3500 -74.7000 5.461994  5.471009  5.492101  5.479041 
10250 10250  5072.2 40.3500 -74.7000 3.862797  1.601567  2.361033  2.892774 
10251 10251  3044.1 40.3500 -74.7000 3.824284  4.133833  4.281976  4.246350 
10252 10252 37324.1 40.3500 -74.7000 5.852250  5.805235  6.011104  6.021266 
10253 10253  3592.7 40.3500 -74.7000 3.862797  1.601567  2.361033  2.892774 
10254 10254  1699.8 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10255 10255 11538.7 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10256 10256  5777.3 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10257 10257  8636.6 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10258 10258  7736.2 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10259 10259  6976.4 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10260 10260  4233.6 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10261 10261  6928.1 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10262 10262 14806.3 30.2672 -97.7431 4.645938  1.808453  2.361033  3.434174 
10

In [30]:
#install.packages("corrgram")

In [14]:
length(numlst)

[1] 144

In [18]:
length(numlst_log)

[1] 52

### C.1. Using lsr packag with correlate function to get the analytic corelations
 

In [36]:
#install.packages("lsr")

In [37]:
#library(lsr)

#### C.1.1 Crating the full coralation matrix with spearman method

In [ ]:
res <- correlate(df, corr.method="spearman")

In [22]:
res

CORRELATIONS
============
- correlation type:  spearman 
- correlations shown only when both variables are numeric

                                        X     ID    sqm    lat    lng El_Max_W1
X                                       .  1.000 -0.003 -0.013  0.012     0.020
ID                                  1.000      . -0.003 -0.013  0.012     0.020
sqm                                -0.003 -0.003      .  0.117 -0.028     0.673
lat                                -0.013 -0.013  0.117      .  0.303     0.128
lng                                 0.012  0.012 -0.028  0.303      .    -0.044
El_Max_W1                           0.020  0.020  0.673  0.128 -0.044         .
El_Max_W2                           0.017  0.017  0.621  0.164 -0.076     0.904
El_Max_W3                           0.015  0.015  0.629  0.172 -0.055     0.913
El_Max_W4                           0.018  0.018  0.651  0.170 -0.044     0.930
El_Max_W5                           0.017  0.017  0.635  0.153 -0.065     0.902
El_Min_W1                           0.037  0.037  0.627  0.140  0.073     0.814
El_Min_W2                          -0.013 -0.013  0.627  0.149 -0.001     0.859
El_Min_W3                          -0.013 -0.013  0.638  0.135  0.020     0.862
El_Min_W4                           0.003  0.003  0.663  0.136  0.010     0.878
El_Min_W5                          -0.001 -0.001  0.634  0.160  0.006     0.857
El_AVG_W1                           0.019  0.019  0.690  0.122  0.006     0.957
El_AVG_W2                           0.005  0.005  0.638  0.154 -0.057     0.904
El_AVG_W3                           0.011  0.011  0.651  0.149 -0.045     0.915
El_AVG_W4                           0.012  0.012  0.682  0.148 -0.027     0.936
El_AVG_W5                           0.015  0.015  0.660  0.146 -0.042     0.915
El_STD_W1                           0.031  0.031  0.493  0.062  0.046     0.645
El_STD_W2                           0.033  0.033  0.592  0.167 -0.105     0.840
El_STD_W3                           0.019  0.019  0.614  0.160 -0.056     0.833
El_STD_W4                           0.031  0.031  0.617  0.182 -0.062     0.824
El_STD_W5                           0.045  0.045  0.600  0.184 -0.071     0.799
ChWt_Max_W1                         0.118  0.118  0.253 -0.215 -0.028     0.400
ChWt_Max_W2                         0.135  0.135  0.258 -0.213 -0.059     0.395
ChWt_Max_W3                         0.080  0.080  0.266 -0.224 -0.054     0.399
ChWt_Max_W4                         0.069  0.069  0.265 -0.212 -0.036     0.395
ChWt_Max_W5                         0.043  0.043  0.261 -0.255 -0.072     0.382
ChWt_Min_W1                         0.104  0.104  0.193 -0.183 -0.091     0.244
ChWt_Min_W2                         0.028  0.028  0.213 -0.241 -0.162     0.270
ChWt_Min_W3                        -0.035 -0.035  0.218 -0.232 -0.246     0.264
ChWt_Min_W4                         0.022  0.022  0.203 -0.148 -0.157     0.271
ChWt_Min_W5                        -0.008 -0.008  0.211 -0.218 -0.159     0.285
ChWt_AVG_W1                         0.110  0.110  0.232 -0.248 -0.037     0.368
ChWt_AVG_W2                         0.112  0.112  0.235 -0.254 -0.074     0.369
ChWt_AVG_W3                         0.064  0.064  0.240 -0.267 -0.076     0.366
ChWt_AVG_W4                         0.068  0.068  0.246 -0.235 -0.045     0.373
ChWt_AVG_W5                         0.029  0.029  0.239 -0.287 -0.079     0.357
ChWt_STD_W1                         0.128  0.128  0.232 -0.201 -0.002     0.371
ChWt_STD_W2                         0.154  0.154  0.240 -0.191 -0.034     0.374
ChWt_STD_W3                         0.099  0.099  0.254 -0.190 -0.036     0.387
ChWt_STD_W4                         0.088  0.088  0.248 -0.183 -0.002     0.372
ChWt_STD_W5                         0.053  0.053  0.241 -0.248 -0.047     0.351
MAX_airTemperature_W1               0.187  0.187 -0.044 -0.473 -0.411    -0.015
MAX_airTemperature_W2               0.152  0.152 -0.037 -0.419 -0.392     0.009
MAX_airTemperature_W3               0.126  0

In [23]:
write.csv(res, file="DF_BGP_OHC_log_RES_07062022.csv")

In [12]:
#res<-read.csv("DF_BGP_OHC_log_RES_07062022.csv")

#### C.1.2 Retriving only the correlation part in to a data frame

In [41]:
RS<-data.frame(res$correlation)

#### C.1.3 Filtering only the row names (=variables) and the outcome column

In [101]:
RS_OC<-RS[c(0,146)]

#### C.1.4 Renaming or crating the variable column 

In [103]:
RS_RN_OC<-tibble::rownames_to_column(RS_OC, "columns") 

In [104]:
RS_RN_OC

columns         El_Nxt_Mnth_Avg_OC
1   X                0.00192427       
2   ID               0.00192427       
3   sqm              0.68080616       
4   lat              0.13274937       
5   lng             -0.03287923       
6   El_Max_W1        0.92117785       
7   El_Max_W2        0.92109698       
8   El_Max_W3        0.93542073       
9   El_Max_W4        0.94959345       
10  El_Max_W5        0.94977919       
11  El_Min_W1        0.83204676       
12  El_Min_W2        0.92521295       
13  El_Min_W3        0.92360721       
14  El_Min_W4        0.91673942       
15  El_Min_W5        0.92337654       
16  El_AVG_W1        0.93025510       
17  El_AVG_W2        0.95072288       
18  El_AVG_W3        0.95968217       
19  El_AVG_W4        0.97183505       
20  El_AVG_W5        0.97616677       
21  El_STD_W1        0.44869278       
22  El_STD_W2        0.78051788       
23  El_STD_W3        0.77043808       
24  El_STD_W4        0.77280087       
25  El_STD_W5        0.76271581       
26  ChWt_Max_W1      0.37364558       
27  ChWt_Max_W2      0.37932188       
28  ChWt_Max_W3      0.38431119       
29  ChWt_Max_W4      0.37816797       
30  ChWt_Max_W5      0.37760188       
... ...             ...               
455 Stm_AVG_W3.mid   0.16390163       
456 Stm_AVG_W3.miss -0.25962415       
457 Stm_AVG_W4.high  0.27845944       
458 Stm_AVG_W4.low  -0.05473360       
459 Stm_AVG_W4.mid   0.16002011       
460 Stm_AVG_W4.miss -0.25981703       
461 Stm_AVG_W5.high  0.27844135       
462 Stm_AVG_W5.low  -0.05861828       
463 Stm_AVG_W5.mid   0.16236394       
464 Stm_AVG_W5.miss -0.26017106       
465 Stm_STD_W1.high  0.27077259       
466 Stm_STD_W1.low  -0.05663314       
467 Stm_STD_W1.mid   0.16861367       
468 Stm_STD_W1.miss -0.25997599       
469 Stm_STD_W2.high  0.27100822       
470 Stm_STD_W2.low  -0.05241988       
471 Stm_STD_W2.mid   0.16639449       
472 Stm_STD_W2.miss -0.26048883       
473 Stm_STD_W3.high  0.27098671       
474 Stm_STD_W3.low  -0.05017039       
475 Stm_STD_W3.mid   0.16469364       
476 Stm_STD_W3.miss -0.25985819       
477 Stm_STD_W4.high  0.27348889       
478 Stm_STD_W4.low  -0.05601713       
479 Stm_STD_W4.mid   0.16681682       
480 Stm_STD_W4.miss -0.25981703       
481 Stm_STD_W5.high  0.27638347       
482 Stm_STD_W5.low  -0.05971809       
483 Stm_STD_W5.mid   0.16731614       
484 Stm_STD_W5.miss -0.26029729

#### C.1.5 Filtering only correlated variables that are less the 70% correlated (more than that "tells the same story")

In [116]:
RS_OC_F<-filter(RS_RN_OC,(abs(RS_RN_OC$"El_Nxt_Mnth_Avg_OC")<0.7))

In [117]:
RS_OC_F

columns               El_Nxt_Mnth_Avg_OC
1   X                      0.001924270      
2   ID                     0.001924270      
3   sqm                    0.680806158      
4   lat                    0.132749371      
5   lng                   -0.032879232      
6   El_STD_W1              0.448692782      
7   ChWt_Max_W1            0.373645577      
8   ChWt_Max_W2            0.379321883      
9   ChWt_Max_W3            0.384311190      
10  ChWt_Max_W4            0.378167966      
11  ChWt_Max_W5            0.377601882      
12  ChWt_Min_W1            0.288416617      
13  ChWt_Min_W2            0.293320575      
14  ChWt_Min_W3            0.272800488      
15  ChWt_Min_W4            0.272366838      
16  ChWt_Min_W5            0.276505047      
17  ChWt_AVG_W1            0.357481920      
18  ChWt_AVG_W2            0.364780344      
19  ChWt_AVG_W3            0.359655431      
20  ChWt_AVG_W4            0.367297701      
21  ChWt_AVG_W5            0.358036700      
22  ChWt_STD_W1            0.342634490      
23  ChWt_STD_W2            0.354702690      
24  ChWt_STD_W3            0.373463626      
25  ChWt_STD_W4            0.358498759      
26  ChWt_STD_W5            0.347508574      
27  MAX_airTemperature_W1 -0.018693231      
28  MAX_airTemperature_W2  0.007593088      
29  MAX_airTemperature_W3 -0.008258187      
30  MAX_airTemperature_W4 -0.009205426      
... ...                   ...               
435 Stm_AVG_W3.mid         0.16390163       
436 Stm_AVG_W3.miss       -0.25962415       
437 Stm_AVG_W4.high        0.27845944       
438 Stm_AVG_W4.low        -0.05473360       
439 Stm_AVG_W4.mid         0.16002011       
440 Stm_AVG_W4.miss       -0.25981703       
441 Stm_AVG_W5.high        0.27844135       
442 Stm_AVG_W5.low        -0.05861828       
443 Stm_AVG_W5.mid         0.16236394       
444 Stm_AVG_W5.miss       -0.26017106       
445 Stm_STD_W1.high        0.27077259       
446 Stm_STD_W1.low        -0.05663314       
447 Stm_STD_W1.mid         0.16861367       
448 Stm_STD_W1.miss       -0.25997599       
449 Stm_STD_W2.high        0.27100822       
450 Stm_STD_W2.low        -0.05241988       
451 Stm_STD_W2.mid         0.16639449       
452 Stm_STD_W2.miss       -0.26048883       
453 Stm_STD_W3.high        0.27098671       
454 Stm_STD_W3.low        -0.05017039       
455 Stm_STD_W3.mid         0.16469364       
456 Stm_STD_W3.miss       -0.25985819       
457 Stm_STD_W4.high        0.27348889       
458 Stm_STD_W4.low        -0.05601713       
459 Stm_STD_W4.mid         0.16681682       
460 Stm_STD_W4.miss       -0.25981703       
461 Stm_STD_W5.high        0.27638347       
462 Stm_STD_W5.low        -0.05971809       
463 Stm_STD_W5.mid         0.16731614       
464 Stm_STD_W5.miss       -0.26029729

#### C.1.6 Same process for the P value (significance) part of the correlation matrix

In [108]:
RS_Pv<-data.frame(res$p.value)

In [109]:
RS_Pv_OC<-RS_Pv[c(0,146)]

In [110]:
RS_Pv_RN_OC<-tibble::rownames_to_column(RS_Pv_OC, "columns") 

In [111]:
RS_Pv_RN_OC

columns         El_Nxt_Mnth_Avg_OC
1   X               1.000000e+00      
2   ID              1.000000e+00      
3   sqm             0.000000e+00      
4   lat             1.251044e-36      
5   lng             1.000000e+00      
6   El_Max_W1       0.000000e+00      
7   El_Max_W2       0.000000e+00      
8   El_Max_W3       0.000000e+00      
9   El_Max_W4       0.000000e+00      
10  El_Max_W5       0.000000e+00      
11  El_Min_W1       0.000000e+00      
12  El_Min_W2       0.000000e+00      
13  El_Min_W3       0.000000e+00      
14  El_Min_W4       0.000000e+00      
15  El_Min_W5       0.000000e+00      
16  El_AVG_W1       0.000000e+00      
17  El_AVG_W2       0.000000e+00      
18  El_AVG_W3       0.000000e+00      
19  El_AVG_W4       0.000000e+00      
20  El_AVG_W5       0.000000e+00      
21  El_STD_W1       0.000000e+00      
22  El_STD_W2       0.000000e+00      
23  El_STD_W3       0.000000e+00      
24  El_STD_W4       0.000000e+00      
25  El_STD_W5       0.000000e+00      
26  ChWt_Max_W1     0.000000e+00      
27  ChWt_Max_W2     0.000000e+00      
28  ChWt_Max_W3     0.000000e+00      
29  ChWt_Max_W4     0.000000e+00      
30  ChWt_Max_W5     0.000000e+00      
... ...             ...               
455 Stm_AVG_W3.mid   8.858839e-58     
456 Stm_AVG_W3.miss 7.558533e-153     
457 Stm_AVG_W4.high 3.043785e-177     
458 Stm_AVG_W4.low   1.900277e-03     
459 Stm_AVG_W4.mid   6.851704e-55     
460 Stm_AVG_W4.miss 4.351038e-153     
461 Stm_AVG_W5.high 3.219497e-177     
462 Stm_AVG_W5.low   1.899242e-04     
463 Stm_AVG_W5.mid   1.260058e-56     
464 Stm_AVG_W5.miss 1.576777e-153     
465 Stm_STD_W1.high 4.756908e-167     
466 Stm_STD_W1.low   6.280785e-04     
467 Stm_STD_W1.mid   2.204583e-61     
468 Stm_STD_W1.miss 2.758999e-153     
469 Stm_STD_W2.high 2.342977e-167     
470 Stm_STD_W2.low   6.957222e-03     
471 Stm_STD_W2.mid   1.132521e-59     
472 Stm_STD_W2.miss 6.332000e-154     
473 Stm_STD_W3.high 2.499459e-167     
474 Stm_STD_W3.low   2.331137e-02     
475 Stm_STD_W3.mid   2.234172e-58     
476 Stm_STD_W3.miss 3.867002e-153     
477 Stm_STD_W4.high 1.297096e-170     
478 Stm_STD_W4.low   9.035391e-04     
479 Stm_STD_W4.mid   5.374560e-60     
480 Stm_STD_W4.miss 4.351038e-153     
481 Stm_STD_W5.high 1.858198e-174     
482 Stm_STD_W5.low   9.617438e-05     
483 Stm_STD_W5.mid   2.220740e-60     
484 Stm_STD_W5.miss 1.097582e-153

#### C.1.7 Filtering the correlations that are siginificant - less then 0.05.

In [112]:
RS_Pv_OC_F<-filter(RS_Pv_RN_OC,(RS_Pv_RN_OC$"El_Nxt_Mnth_Avg_OC"<0.05))

In [113]:
RS_Pv_OC_F

columns         El_Nxt_Mnth_Avg_OC
1   sqm              0.000000e+00     
2   lat              1.251044e-36     
3   El_Max_W1        0.000000e+00     
4   El_Max_W2        0.000000e+00     
5   El_Max_W3        0.000000e+00     
6   El_Max_W4        0.000000e+00     
7   El_Max_W5        0.000000e+00     
8   El_Min_W1        0.000000e+00     
9   El_Min_W2        0.000000e+00     
10  El_Min_W3        0.000000e+00     
11  El_Min_W4        0.000000e+00     
12  El_Min_W5        0.000000e+00     
13  El_AVG_W1        0.000000e+00     
14  El_AVG_W2        0.000000e+00     
15  El_AVG_W3        0.000000e+00     
16  El_AVG_W4        0.000000e+00     
17  El_AVG_W5        0.000000e+00     
18  El_STD_W1        0.000000e+00     
19  El_STD_W2        0.000000e+00     
20  El_STD_W3        0.000000e+00     
21  El_STD_W4        0.000000e+00     
22  El_STD_W5        0.000000e+00     
23  ChWt_Max_W1      0.000000e+00     
24  ChWt_Max_W2      0.000000e+00     
25  ChWt_Max_W3      0.000000e+00     
26  ChWt_Max_W4      0.000000e+00     
27  ChWt_Max_W5      0.000000e+00     
28  ChWt_Min_W1     6.050920e-191     
29  ChWt_Min_W2     6.683673e-198     
30  ChWt_Min_W3     1.047647e-169     
... ...             ...               
220 Stm_AVG_W3.mid   8.858839e-58     
221 Stm_AVG_W3.miss 7.558533e-153     
222 Stm_AVG_W4.high 3.043785e-177     
223 Stm_AVG_W4.low   1.900277e-03     
224 Stm_AVG_W4.mid   6.851704e-55     
225 Stm_AVG_W4.miss 4.351038e-153     
226 Stm_AVG_W5.high 3.219497e-177     
227 Stm_AVG_W5.low   1.899242e-04     
228 Stm_AVG_W5.mid   1.260058e-56     
229 Stm_AVG_W5.miss 1.576777e-153     
230 Stm_STD_W1.high 4.756908e-167     
231 Stm_STD_W1.low   6.280785e-04     
232 Stm_STD_W1.mid   2.204583e-61     
233 Stm_STD_W1.miss 2.758999e-153     
234 Stm_STD_W2.high 2.342977e-167     
235 Stm_STD_W2.low   6.957222e-03     
236 Stm_STD_W2.mid   1.132521e-59     
237 Stm_STD_W2.miss 6.332000e-154     
238 Stm_STD_W3.high 2.499459e-167     
239 Stm_STD_W3.low   2.331137e-02     
240 Stm_STD_W3.mid   2.234172e-58     
241 Stm_STD_W3.miss 3.867002e-153     
242 Stm_STD_W4.high 1.297096e-170     
243 Stm_STD_W4.low   9.035391e-04     
244 Stm_STD_W4.mid   5.374560e-60     
245 Stm_STD_W4.miss 4.351038e-153     
246 Stm_STD_W5.high 1.858198e-174     
247 Stm_STD_W5.low   9.617438e-05     
248 Stm_STD_W5.mid   2.220740e-60     
249 Stm_STD_W5.miss 1.097582e-153

#### C.1.8 Joining the filterd corralation data frame and the P value data frame to get the relevan features (that have less then 70% correlation with the outcome and that the correlation is significant)

In [118]:
RS_Cr_Pv<-merge(x=RS_OC_F, y=RS_Pv_OC_F, by="columns")

In [119]:
RS_Cr_Pv

columns               El_Nxt_Mnth_Avg_OC.x El_Nxt_Mnth_Avg_OC.y
1   Avg_seaLvlPressure_W2 -0.07231479           1.668409e-08       
2   Avg_seaLvlPressure_W3 -0.05077580           1.691838e-02       
3   Avg_seaLvlPressure_W4 -0.06035746           6.438615e-05       
4   Avg_seaLvlPressure_W5 -0.06801168           3.852578e-07       
5   ChWt_AVG_W1            0.35748192          2.869254e-302       
6   ChWt_AVG_W2            0.36478034          8.527724e-316       
7   ChWt_AVG_W3            0.35965543          2.926375e-306       
8   ChWt_AVG_W4            0.36729770           0.000000e+00       
9   ChWt_AVG_W5            0.35803670          2.766616e-303       
10  ChWt_Max_W1            0.37364558           0.000000e+00       
11  ChWt_Max_W2            0.37932188           0.000000e+00       
12  ChWt_Max_W3            0.38431119           0.000000e+00       
13  ChWt_Max_W4            0.37816797           0.000000e+00       
14  ChWt_Max_W5            0.37760188           0.000000e+00       
15  ChWt_Min_W1            0.28841662          6.050920e-191       
16  ChWt_Min_W2            0.29332058          6.683673e-198       
17  ChWt_Min_W3            0.27280049          1.047647e-169       
18  ChWt_Min_W4            0.27236684          3.893554e-169       
19  ChWt_Min_W5            0.27650505          1.278285e-174       
20  ChWt_STD_W1            0.34263449          7.871024e-276       
21  ChWt_STD_W2            0.35470269          3.281473e-297       
22  ChWt_STD_W3            0.37346363           0.000000e+00       
23  ChWt_STD_W4            0.35849876          3.929619e-304       
24  ChWt_STD_W5            0.34750857          2.369399e-284       
25  El_STD_W1              0.44869278           0.000000e+00       
26  hotwater_AVG_W1.high   0.12191997           2.388332e-30       
27  hotwater_AVG_W1.mid    0.07165973           2.721395e-08       
28  hotwater_AVG_W1.miss  -0.09899081           7.468736e-19       
29  hotwater_AVG_W2.high   0.12113608           6.481286e-30       
30  hotwater_AVG_W2.mid    0.07491844           2.276699e-09       
... ...                   ...                  ...                 
201 Stm_Min_W4.high        0.24572631          4.279057e-136       
202 Stm_Min_W4.low         0.06077439           4.953884e-05       
203 Stm_Min_W4.mid         0.10269331           1.523309e-20       
204 Stm_Min_W4.miss       -0.25981703          4.351038e-153       
205 Stm_Min_W5.high        0.23027968          1.091806e-118       
206 Stm_Min_W5.low         0.07440753           3.389832e-09       
207 Stm_Min_W5.mid         0.10159342           4.912271e-20       
208 Stm_Min_W5.miss       -0.26017106          1.576777e-153       
209 Stm_STD_W1.high        0.27077259          4.756908e-167       
210 Stm_STD_W1.low        -0.05663314           6.280785e-04       
211 Stm_STD_W1.mid         0.16861367           2.204583e-61       
212 Stm_STD_W1.miss       -0.25997599          2.758999e-153       
213 Stm_STD_W2.high        0.27100822          2.342977e-167       
214 Stm_STD_W2.low        -0.05241988           6.957222e-03       
215 Stm_STD_W2.mid         0.16639449           1.132521e-59       
216 Stm_STD_W2.miss       -0.26048883          6.332000e-154       
217 Stm_STD_W3.high        0.27098671          2.499459e-167       
218 Stm_STD_W3.low        -0.05017039           2.331137e-02       
219 Stm_STD_W3.mid         0.16469364           2.234172e-58       
220 Stm_STD_W3.miss       -0.25985819          3.867002e-153       
221 Stm_STD_W4.high        0.27348889          1.297096e-170       
222 Stm_STD_W4.low        -0.05601713           9.035391e-04       
223 Stm_STD_W4.mid         0.16681682           5.374560e-60       
224 Stm_STD_W4.miss       -0.25981703          4.351038e-153       
225 Stm_STD_W5.high        0.27638347          1.858198e-174       
226 Stm_STD_W5.low        -0.05971809           9.617438e-05       
227 Stm_STD_W5.mid         0.16731614           2.220740e-60

#### C.1.9 Renaming the columns by their proper names

In [121]:
colnames(RS_Cr_Pv) <- c('variables','OC_Corr','OC_Pval') 

In [122]:
RS_Cr_Pv

variables             OC_Corr     OC_Pval      
1   Avg_seaLvlPressure_W2 -0.07231479  1.668409e-08
2   Avg_seaLvlPressure_W3 -0.05077580  1.691838e-02
3   Avg_seaLvlPressure_W4 -0.06035746  6.438615e-05
4   Avg_seaLvlPressure_W5 -0.06801168  3.852578e-07
5   ChWt_AVG_W1            0.35748192 2.869254e-302
6   ChWt_AVG_W2            0.36478034 8.527724e-316
7   ChWt_AVG_W3            0.35965543 2.926375e-306
8   ChWt_AVG_W4            0.36729770  0.000000e+00
9   ChWt_AVG_W5            0.35803670 2.766616e-303
10  ChWt_Max_W1            0.37364558  0.000000e+00
11  ChWt_Max_W2            0.37932188  0.000000e+00
12  ChWt_Max_W3            0.38431119  0.000000e+00
13  ChWt_Max_W4            0.37816797  0.000000e+00
14  ChWt_Max_W5            0.37760188  0.000000e+00
15  ChWt_Min_W1            0.28841662 6.050920e-191
16  ChWt_Min_W2            0.29332058 6.683673e-198
17  ChWt_Min_W3            0.27280049 1.047647e-169
18  ChWt_Min_W4            0.27236684 3.893554e-169
19  ChWt_Min_W5            0.27650505 1.278285e-174
20  ChWt_STD_W1            0.34263449 7.871024e-276
21  ChWt_STD_W2            0.35470269 3.281473e-297
22  ChWt_STD_W3            0.37346363  0.000000e+00
23  ChWt_STD_W4            0.35849876 3.929619e-304
24  ChWt_STD_W5            0.34750857 2.369399e-284
25  El_STD_W1              0.44869278  0.000000e+00
26  hotwater_AVG_W1.high   0.12191997  2.388332e-30
27  hotwater_AVG_W1.mid    0.07165973  2.721395e-08
28  hotwater_AVG_W1.miss  -0.09899081  7.468736e-19
29  hotwater_AVG_W2.high   0.12113608  6.481286e-30
30  hotwater_AVG_W2.mid    0.07491844  2.276699e-09
... ...                   ...         ...          
201 Stm_Min_W4.high        0.24572631 4.279057e-136
202 Stm_Min_W4.low         0.06077439  4.953884e-05
203 Stm_Min_W4.mid         0.10269331  1.523309e-20
204 Stm_Min_W4.miss       -0.25981703 4.351038e-153
205 Stm_Min_W5.high        0.23027968 1.091806e-118
206 Stm_Min_W5.low         0.07440753  3.389832e-09
207 Stm_Min_W5.mid         0.10159342  4.912271e-20
208 Stm_Min_W5.miss       -0.26017106 1.576777e-153
209 Stm_STD_W1.high        0.27077259 4.756908e-167
210 Stm_STD_W1.low        -0.05663314  6.280785e-04
211 Stm_STD_W1.mid         0.16861367  2.204583e-61
212 Stm_STD_W1.miss       -0.25997599 2.758999e-153
213 Stm_STD_W2.high        0.27100822 2.342977e-167
214 Stm_STD_W2.low        -0.05241988  6.957222e-03
215 Stm_STD_W2.mid         0.16639449  1.132521e-59
216 Stm_STD_W2.miss       -0.26048883 6.332000e-154
217 Stm_STD_W3.high        0.27098671 2.499459e-167
218 Stm_STD_W3.low        -0.05017039  2.331137e-02
219 Stm_STD_W3.mid         0.16469364  2.234172e-58
220 Stm_STD_W3.miss       -0.25985819 3.867002e-153
221 Stm_STD_W4.high        0.27348889 1.297096e-170
222 Stm_STD_W4.low        -0.05601713  9.035391e-04
223 Stm_STD_W4.mid         0.16681682  5.374560e-60
224 Stm_STD_W4.miss       -0.25981703 4.351038e-153
225 Stm_STD_W5.high        0.27638347 1.858198e-174
226 Stm_STD_W5.low        -0.05971809  9.617438e-05
227 Stm_STD_W5.mid         0.16731614  2.220740e-60
228 Stm_STD_W5.miss       -0.26029729 1.097582e-153
229 Tmz.US.Central         0.11717313  9.095864e-28
230 Tmz.US.Pacific        -0.13311275  7.532568e-37

In [123]:
write.csv(RS_Cr_Pv, file="BGP_RS_Cr_Pv_08062022.csv")

In [12]:
#RS_Cr_Pv<-read.csv("BGP_RS_Cr_Pv_08062022.csv")

### C.2. Using Hmisc ("oren's method") packag with correlate function to get the analytic corelations
 

In [45]:
library("Hmisc")
res_oren <- rcorr(as.matrix(sapply(df,as.numeric)),type = "spearman")

In [27]:
flattenCorrMatrix <- function(cormat, pmat) 
    {
      ut <- upper.tri(cormat)
      data.frame(
                    row = rownames(cormat)[row(cormat)[ut]],
                    column = rownames(cormat)[col(cormat)[ut]],
                    cor  =(cormat)[ut],
                    p = pmat[ut]
                )
    }

In [40]:
#res_oren

#### C.2.1 Creating the flatten correlation data frame

In [126]:
CorrMatrix <- flattenCorrMatrix(res_oren$r, res_oren$P)
CorrMatrix

row             column          cor          p           
1      X               ID               1.000000000 0.000000e+00
2      X               sqm             -0.003060354 7.564602e-01
3      ID              sqm             -0.003060354 7.564602e-01
4      X               lat             -0.012972664 1.886154e-01
5      ID              lat             -0.012972664 1.886154e-01
6      sqm             lat              0.117030889 0.000000e+00
7      X               lng              0.011547582 2.418987e-01
8      ID              lng              0.011547582 2.418987e-01
9      sqm             lng             -0.028200913 4.257727e-03
10     lat             lng              0.302674691 0.000000e+00
11     X               El_Max_W1        0.019911296 4.359317e-02
12     ID              El_Max_W1        0.019911296 4.359317e-02
13     sqm             El_Max_W1        0.673477041 0.000000e+00
14     lat             El_Max_W1        0.127932015 0.000000e+00
15     lng             El_Max_W1       -0.043575531 9.962801e-06
16     X               El_Max_W2        0.017298482 7.957900e-02
17     ID              El_Max_W2        0.017298482 7.957900e-02
18     sqm             El_Max_W2        0.620949253 0.000000e+00
19     lat             El_Max_W2        0.163525570 0.000000e+00
20     lng             El_Max_W2       -0.075838422 1.398881e-14
21     El_Max_W1       El_Max_W2        0.903859453 0.000000e+00
22     X               El_Max_W3        0.015278130 1.215371e-01
23     ID              El_Max_W3        0.015278130 1.215371e-01
24     sqm             El_Max_W3        0.628548292 0.000000e+00
25     lat             El_Max_W3        0.172164584 0.000000e+00
26     lng             El_Max_W3       -0.055160044 2.217724e-08
27     El_Max_W1       El_Max_W3        0.912518712 0.000000e+00
28     El_Max_W2       El_Max_W3        0.978669066 0.000000e+00
29     X               El_Max_W4        0.018063480 6.714891e-02
30     ID              El_Max_W4        0.018063480 6.714891e-02
...    ...             ...             ...          ...         
116857 Stm_AVG_W3.low  Stm_STD_W5.miss -0.4199760   0           
116858 Stm_AVG_W3.mid  Stm_STD_W5.miss -0.6126047   0           
116859 Stm_AVG_W3.miss Stm_STD_W5.miss  0.9863332   0           
116860 Stm_AVG_W4.high Stm_STD_W5.miss -0.4151841   0           
116861 Stm_AVG_W4.low  Stm_STD_W5.miss -0.4199760   0           
116862 Stm_AVG_W4.mid  Stm_STD_W5.miss -0.6126047   0           
116863 Stm_AVG_W4.miss Stm_STD_W5.miss  0.9865429   0           
116864 Stm_AVG_W5.high Stm_STD_W5.miss -0.4184513   0           
116865 Stm_AVG_W5.low  Stm_STD_W5.miss -0.4244141   0           
116866 Stm_AVG_W5.mid  Stm_STD_W5.miss -0.6182481   0           
116867 Stm_AVG_W5.miss Stm_STD_W5.miss  0.9991575   0           
116868 Stm_STD_W1.high Stm_STD_W5.miss -0.4028675   0           
116869 Stm_STD_W1.low  Stm_STD_W5.miss -0.4297315   0           
116870 Stm_STD_W1.mid  Stm_STD_W5.miss -0.5909095   0           
116871 Stm_STD_W1.miss Stm_STD_W5.miss  0.9713233   0           
116872 Stm_STD_W2.high Stm_STD_W5.miss -0.4071074   0           
116873 Stm_STD_W2.low  Stm_STD_W5.miss -0.4310462   0           
116874 Stm_STD_W2.mid  Stm_STD_W5.miss -0.5871975   0           
116875 Stm_STD_W2.miss Stm_STD_W5.miss  0.9719572   0           
116876 Stm_STD_W3.high Stm_STD_W5.miss -0.4149350   0           
116877 Stm_STD_W3.low  Stm_STD_W5.miss -0.4314621   0           
116878 Stm_STD_W3.mid  Stm_STD_W5.miss -0.6027730   0           
116879 Stm_STD_W3.miss Stm_STD_W5.miss  0.9861236   0           
116880 Stm_STD_W4.high Stm_STD_W5.miss -0.4151841   0           
116881 Stm_STD_W4.low  Stm_STD_W5.miss -0.4297579   0           
116882 Stm_STD_W4.mid  Stm_STD_W5.miss -0.6044294   0           
116883 Stm_STD_W4.miss Stm_STD_W5.miss  0.9865429   0           
116884 Stm_STD_W5.high Stm_STD_W5.miss -0.4189094   0           
116885 Stm_STD_W5.low  Stm_STD_W5.miss -0.4355422   0           
116886 Stm_STD_W5.mid  Stm_STD_W5.miss -0.

In [35]:
write.csv(CorrMatrix, file="DF_BGP_OHC_log_corrMat_07062022.csv")

In [12]:
#CorrMatrix<-read.csv("DF_BGP_OHC_log_corrMat_07062022.csv")

#### C.2.2 Filtering to correlation less then 70% (higher over fitt) and significant (less then 0.05)

In [135]:
FilterCorrMatrix <-  filter(CorrMatrix , (abs(cor)<0.7) & (p<0.05) & (column =="El_Nxt_Mnth_Avg_OC"))
FilterCorrMatrix

row                   column             cor         p           
1   sqm                   El_Nxt_Mnth_Avg_OC  0.68080616 0.000000e+00
2   lat                   El_Nxt_Mnth_Avg_OC  0.13274937 0.000000e+00
3   lng                   El_Nxt_Mnth_Avg_OC -0.03287923 8.596609e-04
4   El_STD_W1             El_Nxt_Mnth_Avg_OC  0.44869278 0.000000e+00
5   ChWt_Max_W1           El_Nxt_Mnth_Avg_OC  0.37364558 0.000000e+00
6   ChWt_Max_W2           El_Nxt_Mnth_Avg_OC  0.37932188 0.000000e+00
7   ChWt_Max_W3           El_Nxt_Mnth_Avg_OC  0.38431119 0.000000e+00
8   ChWt_Max_W4           El_Nxt_Mnth_Avg_OC  0.37816797 0.000000e+00
9   ChWt_Max_W5           El_Nxt_Mnth_Avg_OC  0.37760188 0.000000e+00
10  ChWt_Min_W1           El_Nxt_Mnth_Avg_OC  0.28841662 0.000000e+00
11  ChWt_Min_W2           El_Nxt_Mnth_Avg_OC  0.29332058 0.000000e+00
12  ChWt_Min_W3           El_Nxt_Mnth_Avg_OC  0.27280049 0.000000e+00
13  ChWt_Min_W4           El_Nxt_Mnth_Avg_OC  0.27236684 0.000000e+00
14  ChWt_Min_W5           El_Nxt_Mnth_Avg_OC  0.27650505 0.000000e+00
15  ChWt_AVG_W1           El_Nxt_Mnth_Avg_OC  0.35748192 0.000000e+00
16  ChWt_AVG_W2           El_Nxt_Mnth_Avg_OC  0.36478034 0.000000e+00
17  ChWt_AVG_W3           El_Nxt_Mnth_Avg_OC  0.35965543 0.000000e+00
18  ChWt_AVG_W4           El_Nxt_Mnth_Avg_OC  0.36729770 0.000000e+00
19  ChWt_AVG_W5           El_Nxt_Mnth_Avg_OC  0.35803670 0.000000e+00
20  ChWt_STD_W1           El_Nxt_Mnth_Avg_OC  0.34263449 0.000000e+00
21  ChWt_STD_W2           El_Nxt_Mnth_Avg_OC  0.35470269 0.000000e+00
22  ChWt_STD_W3           El_Nxt_Mnth_Avg_OC  0.37346363 0.000000e+00
23  ChWt_STD_W4           El_Nxt_Mnth_Avg_OC  0.35849876 0.000000e+00
24  ChWt_STD_W5           El_Nxt_Mnth_Avg_OC  0.34750857 0.000000e+00
25  MAX_dewTemperature_W1 El_Nxt_Mnth_Avg_OC -0.02066958 3.618442e-02
26  MAX_seaLvlPressure_W5 El_Nxt_Mnth_Avg_OC -0.02495425 1.143161e-02
27  MAX_windDirection_W1  El_Nxt_Mnth_Avg_OC -0.02417890 1.426135e-02
28  MAX_windDirection_W2  El_Nxt_Mnth_Avg_OC -0.04674794 2.137614e-06
29  MAX_windDirection_W3  El_Nxt_Mnth_Avg_OC -0.02510573 1.094096e-02
30  MAX_windDirection_W4  El_Nxt_Mnth_Avg_OC -0.02989411 2.444703e-03
... ...                   ...                ...         ...         
55  Avg_dewTemperature_W5 El_Nxt_Mnth_Avg_OC -0.02164511 2.825401e-02
56  Avg_seaLvlPressure_W1 El_Nxt_Mnth_Avg_OC -0.02652093 7.186744e-03
57  Avg_seaLvlPressure_W2 El_Nxt_Mnth_Avg_OC -0.07231479 2.171596e-13
58  Avg_seaLvlPressure_W3 El_Nxt_Mnth_Avg_OC -0.05077580 2.620648e-07
59  Avg_seaLvlPressure_W4 El_Nxt_Mnth_Avg_OC -0.06035746 9.233903e-10
60  Avg_seaLvlPressure_W5 El_Nxt_Mnth_Avg_OC -0.06801168 5.193179e-12
61  Avg_windSpeed_W1      El_Nxt_Mnth_Avg_OC -0.03974122 5.603627e-05
62  Avg_windSpeed_W3      El_Nxt_Mnth_Avg_OC -0.02537758 1.010716e-02
63  Avg_windSpeed_W5      El_Nxt_Mnth_Avg_OC  0.03337499 7.166844e-04
64  Std_airTemperature_W1 El_Nxt_Mnth_Avg_OC -0.02566604 9.284740e-03
65  Std_airTemperature_W4 El_Nxt_Mnth_Avg_OC -0.04179159 2.265763e-05
66  Std_airTemperature_W5 El_Nxt_Mnth_Avg_OC -0.03534991 3.391143e-04
67  Std_dewTemperature_W2 El_Nxt_Mnth_Avg_OC  0.03005604 2.315045e-03
68  Std_dewTemperature_W3 El_Nxt_Mnth_Avg_OC  0.03156023 1.378743e-03
69  Std_dewTemperature_W5 El_Nxt_Mnth_Avg_OC  0.02622407 7.861381e-03
70  Std_seaLvlPressure_W1 El_Nxt_Mnth_Avg_OC  0.09013124 0.000000e+00
71  Std_seaLvlPressure_W2 El_Nxt_Mnth_Avg_OC  0.06038568 9.069119e-10
72  Std_seaLvlPressure_W3 El_Nxt_Mnth_Avg_OC  0.04446785 6.527603e-06
73  Std_seaLvlPressure_W4 El_Nxt_Mnth_Avg_OC  0.03663631 2.040762e-04
74  Std_seaLvlPressure_W5 El_Nxt_Mnth_Avg_OC  0.06803139 5.120349e-12
75  Std_windDirection_W1  El_Nxt_Mnth_Avg_OC -0.05999935 1.159620e-09
76  Std_windDirection_W2  El_Nxt_Mnth_Avg_OC -0.02601482 8.370436e-03
77  Std_windDirection_W3  El_Nxt_Mnth_Avg_OC -0.04844611 8.999481e-07
78  Std_windDirection_W4  El_Nxt_Mnth_Avg_OC -0.03815161 1.098955e-04
79  Std_windDirection_W5  El_Nxt_Mnth_Avg_OC -0.05549329 1.823680e-08
80  Std_windSp

In [136]:
write.csv(FilterCorrMatrix, file="BGP_oren_Corl_filt-08062022.csv")
